!! Create new colonization data table and save it to load folder when update

# Rogue Trader Colonization Events

## Introduction

### Library

In [865]:
import pandas as pd
import numpy as np
import json
import os
import re
from bs4 import BeautifulSoup
import jsonpath_ng as jp
pd.set_option('display.max_columns', None)
pd.set_option('max_colwidth', 300)
import warnings
import openpyxl
warnings.filterwarnings('ignore')
import flatten_json as fj

### Functions

In [866]:
# Fuction to show missed data in a table
def missing_values_tab(df):
    #Count missed values
    mis_val = df.isnull().sum()
    #Count share of missed values of all data 
    mis_val_percent = round(100 * df.isnull().sum() / len(df),2)
    
    mv_table = pd.concat([mis_val, mis_val_percent], axis=1)
    
    mv_table = mv_table.rename(columns = {0 : 'missed_values', 1 : '%_of_all'})
    
    mv_table['data_type'] = df.dtypes
    mv_table = mv_table[mv_table.iloc[:,1]!=0].sort_values(by='missed_values',ascending=False)
    print ("Dataframe contains " + str(df.shape[1]) + " columns and " + str(df.shape[0]) + " strings.\n")
    print("It has  " + str(mv_table.shape[0]) +" columns with missed values")    
    return display(mv_table) 

In [867]:
def extract_num_from_string(name):
    """Function to extract number from string"""
    return int(''.join(filter(str.isdigit,name)))

In [868]:
def camel_case_split(str): 
    return re.findall(r'[A-Z](?:[a-z]+|[A-Z]*(?=[A-Z]|$))', str)

In [869]:
def key_builder(row):
            """Function to split the names of stringkey columns responsible for text information like
            'Data_m_Description_Shared_stringkey',
            'Data_m_Description_m_Key',
            'Data_m_DisplayName_Shared_stringkey',
            'Data_m_DisplayName_m_Key' 
            into separate keys for processing"""
            return re.findall(r'[A-Za-z]+(?=_m_)|m_[A-Za-z]+(?=_)|Shared(?=_)|stringkey$|m_[A-Za-z]+$', row)  

In [870]:
def column_name_formatter(col):
    """used for delete prefixes 'Data_m_' in columns' names
    """ 
    if 'Data' in col:
        parts = col.split('_')
        new_name = parts[-1]
        return new_name
    else:
        return col

In [871]:
# Функция для очистки строк от префикса '!bp_'
def clear_rows(row):
        
    if re.match('^\!bp_\w+', str(row)):
        tmp = row.split('_')
        new_value = tmp[1]        
        return new_value
    else:
        return row

In [872]:
def show_uniques(df):
    for col in df.columns[1:-1]:
        try:
            print(col, ':    ', df[col].unique(),'\n')
        except:
            continue

In [873]:
#Function to extract json into dataframes
def create_df(filelist):
    recipes_df = pd.DataFrame()
    dfs_list = []
    for file in filelist:
        with open(file) as user_file:
            file_contents = user_file.read()
            data = json.loads(file_contents)
            dic = (fj.flatten(data))
            df = pd.DataFrame.from_dict(dic, orient='index')
            dfs_list.append(df)
    for df in dfs_list:
        recipes_df = recipes_df.join(df, how = 'outer',lsuffix = 'x_',rsuffix = 'y_')
    #assign new column names
    column_numbers = list(range(len(recipes_df.columns)))
    recipes_df.columns = column_numbers
    #fill Nans
    #recipes_df = recipes_df.fillna(0)
    #remove prefix '!bp_'
    for col in recipes_df.columns:
        recipes_df[col] = recipes_df[col].apply(clear_rows)  
    #transpose dataframe
    recipes_df = recipes_df.T
    #-------------------------------------
    cols_to_drop = []
    for col in recipes_df.columns:
        if 'VisualParameters' in col or 'FXSettings' in col: #drop columns with visual parameters
            cols_to_drop.append(col)
        elif 'Data_Comment' in col or 'PrototypeLink' in col:  #drop columns with dev comments
            cols_to_drop.append(col)
        elif 'Meta_ShadowDeleted' in col: #drop trash column
            cols_to_drop.append(col)
        elif 'JsonPath' in col or 'PropertyPath' in col or 'OwnerString' in col: #drop columns with fileways
            cols_to_drop.append(col)
        elif 'UI' in col or 'Sound' in col or 'Icon' in col: #drop columns with sound, ui properties
            cols_to_drop.append(col)
    recipes_df = recipes_df.drop(cols_to_drop, axis = 1)
    #add column Filepath
    recipes_df['Filepath'] = filelist
    return recipes_df

In [874]:
# Function to get rid of characters between curly brackets
""" Sometimes not working correctly
def format_description(row):
    if '{' in row:
        row = re.sub(r'\s*{.*}\s*','',row)
    return row
"""
def format_description(row):   
    openining_braces = '\{'
    closing_braces = '\}'
    text_between = '.*?'
    x = re.sub(f'[{openining_braces}]{text_between}[{closing_braces}]','',row)
    #get rid of html tags
    x = re.sub('<[^>]*>',"",x)
    return x

In [875]:
#Function to find columns with string keys
def match_pattern(row):
        if re.match('^\w{8}-\w{4}-\w{4}-\w{4}-\w{12}$', str(row)):
            return True   
        else:
            return False
   
        
match_pattern('ca24785c24384d142a6c22d7585bb3a6, BlueprintWeaponEnchantment')
"""
#finding columns with string keys
stringkey_cols = []
for col in weapon_enchants_df.columns:    
        a = weapon_enchants_df[col].apply(match_pattern).any()
        if a:            
            stringkey_cols.append(col)
print(stringkey_cols)   
    """

'\n#finding columns with string keys\nstringkey_cols = []\nfor col in weapon_enchants_df.columns:    \n        a = weapon_enchants_df[col].apply(match_pattern).any()\n        if a:            \n            stringkey_cols.append(col)\nprint(stringkey_cols)   \n    '

In [876]:
#Function to find columns with asset ids
def find_assetIds_cols(row):
        if re.match('^[a-zA-Z0-9]{32}$', str(row)):
            return True   
        else:
            return False      

"""
#finding columns with asset ids
assetIds_cols = []
for col in weapon_enchants_df.columns:    
        a = weapon_enchants_df[col].apply(find_assetIds_cols).any()
        if a:            
            assetIds_cols.append(col)
print(assetIds_cols)   
    """

'\n#finding columns with asset ids\nassetIds_cols = []\nfor col in weapon_enchants_df.columns:    \n        a = weapon_enchants_df[col].apply(find_assetIds_cols).any()\n        if a:            \n            assetIds_cols.append(col)\nprint(assetIds_cols)   \n    '

In [877]:
#Function to find columns with context actions, containing $ signs
def find_context_columns(row):
        if re.match('^\$[A-Za-z0-9]+\$\w{8}-\w{4}-\w{4}-\w{4}-\w{12}$', str(row)):
            return True   
        else:
            return False
"""
#find columns with rows containing $$
context_cols = []
for col in weapon_enchants_df.columns:    
        a = weapon_enchants_df[col].apply(find_context_columns).any()
        if a:            
            context_cols.append(col)
print(context_cols)   
    """

'\n#find columns with rows containing $$\ncontext_cols = []\nfor col in weapon_enchants_df.columns:    \n        a = weapon_enchants_df[col].apply(find_context_columns).any()\n        if a:            \n            context_cols.append(col)\nprint(context_cols)   \n    '

In [878]:
def find_item_type(row):
    """Function to return item type from the column "Data_$type"
    """
    tmp = str(row).split(',')
    data_type = tmp[1]    
    parts = re.split('(?<=[a-z])(?=[A-Z])', data_type)
    item_type = parts[-1]   
    return item_type

In [879]:
def create_text_columns(df, index_df, columns_in, column_out, format_text=False):
    """ Function to create text columns with names and descriptions got from 
        stringkeys in index file in the form of dict
        """
    # list of columns with string keys of items' names
    cols_names = columns_in
    #created column
    column_out = str(column_out )
    index_df = index_df # index_dict object got from parsing json file with text information
    index_dict = dict(zip(index_df['index'],index_df['text'])) #dict for mapping text information between two tables    
    
    #_____________________________Get items names and descriptions__________________________ 
    
    for col in cols_names:
        list_of_ids = df[col].unique() # list of stringkeys
        #filter out empty elements
        list_of_ids = list(filter(None,list_of_ids))
        for id in list_of_ids:
            try: #if stringkey is in index file return text
                df.loc[df[col]==id, column_out] = df[col].map(index_dict)
            except: #if not return empty row
                df.loc[df[col]==id, column_out] = ''          
    
         # fill missed values with empty row       
    df[column_out] = df[column_out].fillna('')
    # format description to get rid of {}
    if format_text == True:
        df[column_out] = df[column_out].apply(format_description)

   
    return df

In [880]:
def find_property_cols(row):
    #if  re.match('^Data_Components_[0-9]_\$type$',row) or re.match('^Data_Components_[0-9]_m_(?:Fact|Facts)(?:$|_[0-9]$)',row):   
    if re.match('^Data_Components_[0-9]_(?:\$type$|m_(?:Fact|Facts)(?:$|_[0-9]$))',str(row)):
        return True
    else:
        return False

"""
#find columns with rows containing property values
property_cols = []
for col in equip_items_df.columns:    
        a = equip_items_df[col].apply(find_property_cols).any()
        if a:            
            property_cols.append(col)
print(property_cols)   
    """    

'\n#find columns with rows containing property values\nproperty_cols = []\nfor col in equip_items_df.columns:    \n        a = equip_items_df[col].apply(find_property_cols).any()\n        if a:            \n            property_cols.append(col)\nprint(property_cols)   \n    '

In [881]:
def find_properties(row):
    #if  re.match('^Data_Components_[0-9]_\$type$',row) or re.match('^Data_Components_[0-9]_m_(?:Fact|Facts)(?:$|_[0-9]$)',row):   
    if re.match('^Data_Components_[0-9]_(?:\$type$|m_[A-Za-z]+(?:$|_[0-9]$))',str(row)):
        return True
    else:
        return False
def select_columns(df, keywords):
    """function to select columns to keep from a dataframe and return 4 lists of
        stringkey columns, assetids columns, misc columns and combined list of columns
    Arguments: df - dataframe to choose columns from, 
                keywords - list of keywords or names of columns to select for misc list    
    """
    selected_cols = [] # list of needed columns
    assetIds_cols = [] #list of columns with asset ids
    stringkey_cols = [] # list of columns with string keyes
    misc_cols = [] # list of misc columns
    property_cols = [] # list of property columns
    intro_cols = []   # first columns: AssetId and Data_$type in any table

    def find_ids(col):
        if re.match('^[a-z0-9]{32}(?:$|[, A-Za-z])', str(col)):
            return True
        else:
            return False      

    #find columns with asset ids
    for col in df.columns:
        if col !='AssetId':
            a = df[col].apply(find_assetIds_cols).any()
            if a:            
                assetIds_cols.append(col)
        else:
            intro_cols.append(col)

    #find columns with string keys
    for col in df.columns:    
        a = df[col].apply(match_pattern).any()
        if a:            
            stringkey_cols.append(col)
    
    #find columns with rows containing property values

    for col in df.columns: 
        # if name of the column is according to the pattern   
        if  re.match('^Data_Components_[0-9]+_(?:\$type$|m_[A-Za-z]+(?:$|_[0-9]+$))',str(col)):
            a = df[col].apply(find_ids).any()
            if a:                        
        #and its values are assetIds keys  add to property list                 
                property_cols.append(col) 
      
    # find miscellanious columns
    if len(keywords)>0:
        keywords = keywords
        for keyword in keywords:
            for col in df.columns:
                if keyword in col:
                    misc_cols.append(col)
    #else:
        #misc_cols = [d for d in df.columns if d not in assetIds_cols if d not in stringkey_cols if d not in property_cols]
    #update assetIds_cols
    assetIds_cols = [d for d in assetIds_cols if d not in property_cols]
    #Must- have columns, 'AssetId' and 'Data_$type'
    intro_cols.append(df.columns[1]) #add Data_$type
    #create combined list            
    selected_cols = intro_cols + assetIds_cols+ property_cols + stringkey_cols + misc_cols + ['Filepath']
      
    return selected_cols, assetIds_cols, stringkey_cols, property_cols, misc_cols

In [882]:
def find_stringkeys(row):      
        try:
            row = row.strip()
            with open(row) as asset_file:           
                file_contents = asset_file.read()
                data = json.loads(file_contents)
                try:
                    if data['Data']['m_Name']['Shared'] is not None:
                        key_list = [data['Data']['m_Name']['m_Key'], data['Data']['m_Name']['Shared']['stringkey']]
                        for key in key_list:                     
                            a = match_pattern(key) 
                            if a:                 
                                return key
                    else:
                        key = data['Data']['m_Name']['m_Key']
                        return key
                except Exception as err:
                    print(f'Unexpected {err=}, {type(err)=}',row)
                #print(data['Data']['m_DisplayName']['Shared'])
                
        except:
            return '' 

In [883]:
def get_text_info(df, map_df, index_df, columns_in, keylist = None, format_text=False, add_aggr_col = False):
    """ Function to create text columns with names and descriptions. Works on columns with asset ids
        and get filenames of those asset ids in asset_df and then look into files to extract strinkeys,
        max length of keylist is 4
        """
    # list of columns with string keys of items' names
    cols_names = columns_in
    #created column        
    # map_df - a dataframe for mapping    
    assets_dict = dict(zip(map_df.iloc[:,0],map_df.iloc[:,1])) #dict for mapping text information between two tables
    #reference to dataframe go from localization file    
    
    def find_parent(D):
        """find first key path to value containing stringkey"""    
        for k, v in D.items():        
            if isinstance(v,dict):
                parent = find_parent(v)
                if parent:
                    return [k] + parent
            elif match_pattern(v):                
                return [k]
    def find_stringkeys(row, keylist = None):    
        try:
            row = row.strip()
            with open(row) as asset_file:           
                file_contents = asset_file.read()
                data = json.loads(file_contents)
                try: 
                    if keylist is None:                   
                        keylist = find_parent(data)
                        if len(keylist)==3:
                            key = data[keylist[0]][keylist[1]][keylist[2]]
                            return key
                        else:
                            key = data[keylist[0]][keylist[1]][keylist[2]][keylist[3]]
                            return key
                    else:
                        if len(keylist)==1:
                            key = data[keylist[0]]
                            return key
                        if len(keylist)==2:
                            key = data[keylist[0]][keylist[1]]
                            return key
                        if len(keylist)==3:
                            key = data[keylist[0]][keylist[1]][keylist[2]]
                            return key
                        else:
                            key = data[keylist[0]][keylist[1]][keylist[2]][keylist[3]]
                            return key                  
                except Exception as err:
                    print(f'Unexpected {err=}, {type(err)=}',row)                
                
        except:
            return ''      
    
    #_____________________________Get items names and descriptions__________________________ 
    temp_list = []
    columns_out = []
    for col in cols_names:                
                df[col] = df[col].str.strip()         
                filenames_series = df[col].map(assets_dict)
                df['{}_stringkey'.format(col)]  = filenames_series.apply(find_stringkeys, keylist)
                temp_list.append('{}_stringkey'.format(col))
                text_column_name = '{}_text'.format(col)
                columns_out.append(text_column_name)   
    for i in range(len(columns_out)):
         col_in = [temp_list[i]]
         df = create_text_columns(df, index_df, col_in, columns_out[i], format_text = True)
    #drop created stringkey cols
    df = df.drop(columns = temp_list, axis = 1)
    if add_aggr_col == True:
        df['All_Items'] =df[columns_out].agg(sum)  
    return df, columns_out

In [884]:
def drop_trash_columns (df):
    df = df.loc[:,~df.where(df.astype(bool)).isna().all(axis = 0)]
    return df

### Folders and Files

**Main files:**  

In [885]:
#folder with the gameobjects' parameters
work_folder = r'e:\Steam\RogueTrader\WorkFolder\Blueprints'
# file with the english localization
index_file = r'e:\Steam\RogueTrader\Localization\enGB.json'
#file with the russian localization
index_file_ru = r'e:\Steam\RogueTrader\Localization\ruRU.json'
save_folder = r'e:\Steam\RogueTrader\SaveFolder'
load_folder = r'e:\Steam\RogueTrader\LoadFolder'
# global map folder
folder_global_map = r'e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps'

**load support tables**:  

In [886]:
#loading support dataframes
assets_df = pd.read_csv(load_folder + r'\assets_df.csv')
index_df = pd.read_csv(load_folder + r'\index_df.csv')
index_df_ru = pd.read_csv(load_folder + r'\index_df_ru.csv')

In [887]:
index_df = index_df.fillna('')
index_df_ru = index_df_ru.fillna('')

## Work Part

### Create colonization main sheet

In [888]:
list_of_colonization_files = {} # dictionary of global map folder files with subfolders as keys
#print([x[0] for x in os.walk(folder_global_map)])
dir_list = next(os.walk(folder_global_map))[1]
print(dir_list)
for dir in dir_list:
    list_of_dir_files = []
    for root,dirs,files in os.walk('{}\\{}'.format(folder_global_map,dir)):
        for file in files:
            list_of_dir_files.append(os.path.join(root, file))
    list_of_colonization_files[dir] = list_of_dir_files

print(list_of_colonization_files.keys())


['Anomalies', 'Colonization', 'ExplorationLoot', 'KoronusExpanseGM', 'Points', 'StarSystemObjects', 'StarSystems', 'WarpTravel']
dict_keys(['Anomalies', 'Colonization', 'ExplorationLoot', 'KoronusExpanseGM', 'Points', 'StarSystemObjects', 'StarSystems', 'WarpTravel'])


<span style ="color:yellow">Create colonization table:</span>

In [889]:
#colonization_data = create_df(list_of_colonization_files['Colonization'])

    

In [890]:
#save colonization_data
#colonization_data.to_csv(save_folder + r'\colonization_data.csv', index=False)

In [891]:
colonization_data = pd.read_csv(load_folder + r'\colonization_data.csv')

In [892]:
display(colonization_data.head())
print(colonization_data.shape)

AssetId  \
0  7731f4c089ed4b988e21e32ee3974fd0   
1  14db48fd3df8423bbfb39dff565d8dbc   
2  4ffaa1fe758f497ca90ae9301b37abaa   
3  893cdc250bb84fe98ceb450996eb04d7   
4  28a6b07e809d46b0b56aa68c14bc0c93   

                                                            Data_$type  \
0          d5360515209f38448bb1eed62787cfca, BlueprintColonyEventsRoot   
1                57e97e3d284c4783a511aed21a5c247c, BlueprintColonyRoot   
2         cba5145ec4e04f15ab3f3215b26eee0f, BlueprintItemResourceMiner   
3  88f183371f584e10b325337ce9862d68, BlueprintPointOfInterestBookEvent   
4               cae39a2d3a2a4164b8d42c8b4180f442, BlueprintColonyTrait   

   Data_AccessibilityModifier Data_ActionsOnFinish_Actions  \
0                         NaN                          NaN   
1                         NaN                          NaN   
2                         NaN                          NaN   
3                         NaN                          NaN   
4                         NaN                          NaN   

  Data_ActionsOnFinish_Actions_0_$type Data_ActionsOnFinish_Actions_0_Etude  \
0                                  NaN                                  NaN   
1                                  NaN                                  NaN   
2                                  NaN                                  NaN   
3                                  NaN                                  NaN   
4                                  NaN                                  NaN   

   Data_ActionsOnFinish_Actions_0_EtudeEvaluator  \
0                                            NaN   
1                                            NaN   
2                                            NaN   
3                                            NaN   
4                                            NaN   

  Data_ActionsOnFinish_Actions_0_Evaluate  \
0                                     NaN   
1                                     NaN   
2                                     NaN   
3                                     NaN   
4                                     NaN   

  Data_ActionsOnFinish_Actions_0_Trait  \
0                                  NaN   
1                                  NaN   
2                                  NaN   
3                                  NaN   
4                                  NaN   

  Data_ActionsOnFinish_Actions_0_UnlockIfNot  \
0                                        NaN   
1                                        NaN   
2                                        NaN   
3                                        NaN   
4                                        NaN   

  Data_ActionsOnFinish_Actions_0_Value_$type  \
0                                        NaN   
1                                        NaN   
2                                        NaN   
3                                        NaN   
4                                        NaN   

   Data_ActionsOnFinish_Actions_0_Value_Value  \
0                                         NaN   
1                                         NaN   
2                                         NaN   
3                                         NaN   
4                                         NaN   

  Data_ActionsOnFinish_Actions_0_Value_name  \
0                                       NaN   
1                                       NaN   
2                                       NaN   
3                                       NaN   
4                                       NaN   

  Data_ActionsOnFinish_Actions_0_m_Chronicle  \
0                                        NaN   
1                                        NaN   
2                                        NaN   
3                                        NaN   
4                                        NaN   

  Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint  \
0                                              NaN   
1                                              NaN   
2                                              NaN   
3 

(2742, 2992)


In [893]:
print(colonization_data['Data_$type'].unique())

['d5360515209f38448bb1eed62787cfca, BlueprintColonyEventsRoot'
 '57e97e3d284c4783a511aed21a5c247c, BlueprintColonyRoot'
 'cba5145ec4e04f15ab3f3215b26eee0f, BlueprintItemResourceMiner'
 '88f183371f584e10b325337ce9862d68, BlueprintPointOfInterestBookEvent'
 'cae39a2d3a2a4164b8d42c8b4180f442, BlueprintColonyTrait'
 '5bdf41aff5c94c189e3311d82784844a, BlueprintPlanetBuilding'
 'aa1696d025c449f18968245aa30f56fd, BlueprintColony'
 '52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList'
 'df78945bb9f434e40b897758499cb714, BlueprintAnswer'
 'eea0d7fdafd8fe047a81a3208e5ed9ab, BlueprintCueSequence'
 '8eee9d45ddcfa614d99610c1892993e3, BlueprintCue'
 'c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog'
 '72b026d82361459581a0cb453c0385cb, BlueprintColonyChronicle'
 '6091ddca960a4d1459ac23e917c21d7d, BlueprintSequenceExit'
 'ab803aaa7a173f84e9172870c15e7493, BlueprintCheck'
 '06e9a18b1f15bcf41b3a0ce1a2a0dfdd, BlueprintUnlockableFlag'
 'a7423956769d433f9a182d3e557ad427, BlueprintColonyEvent'
 'af36c53

### Colonies

In [894]:
colonies_df = colonization_data[colonization_data['Data_$type']=='aa1696d025c449f18968245aa30f56fd, BlueprintColony'].reset_index(drop=True)
#Drop columns containing only nans, empty lists, empty dicts
colonies_df = drop_trash_columns(colonies_df)
#Drop unused columns
colonies_df = colonies_df.drop(columns=['Data_Components','Data_Name_Shared_assetguid','Data_PlanetVisual'], axis = 1)
print(colonies_df.shape)
display(missing_values_tab(colonies_df))

(5, 38)
Dataframe contains 38 columns and 5 strings.

It has  6 columns with missed values


missed_values  %_of_all data_type
Data_ResourcesProducedFromStart_2_Count                 4      80.0   float64
Data_ResourcesProducedFromStart_2_Resource              4      80.0    object
Data_ResourcesProducedFromStart_3_Count                 4      80.0   float64
Data_ResourcesProducedFromStart_3_Resource              4      80.0    object
Data_ResourcesProducedFromStart_1_Count                 3      60.0   float64
Data_ResourcesProducedFromStart_1_Resource              3      60.0    object

None

In [895]:
#fill missed values in columns 
int_columns = ['Data_ResourcesProducedFromStart_0_Count','Data_ResourcesProducedFromStart_1_Count', 
               'Data_ResourcesProducedFromStart_2_Count','Data_ResourcesProducedFromStart_3_Count']
for  col in int_columns:
    colonies_df[col] = colonies_df[col].fillna(0)
colonies_df[int_columns] = colonies_df[int_columns].astype('int')
#fill other nans with empty rows
colonies_df = colonies_df.fillna('')

In [896]:
colonies_df.head()

AssetId  \
0  e433f1613297486cb6ddec834f37dd95   
1  883a5e2be9384e9f941ec3abf65f5d73   
2  876fc13fdc10492b8444e045ac8f9ecc   
3  0a8a3c9ea1b444118d33ebcc24db10f7   
4  47400e8140a3434882459f2c95b54b7f   

                                          Data_$type  \
0  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
1  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
2  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
3  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
4  aa1696d025c449f18968245aa30f56fd, BlueprintColony   

             Data_Name_Shared_stringkey                   Data_Projects_0  \
0  a3676728-2f4a-4f85-ab22-911b2d2aaece  bffe6bc0b8134433b1d724f472e7d72f   
1  b9e7ce61-aed3-4265-8c58-01448b1867f6  0e0dbf4dd52545ad82f58eba241bb61b   
2  335d4de0-5b78-452f-9656-dcbcc9850d41  221c15362f084814b4937debf0757e94   
3  902ea4b0-b882-4cd0-b9f1-ea86bff28e04  b0243a87cbcc47ff894f104857016310   
4  3b17dd0b-b718-462d-bc7e-3cbd35f61f40  191508697446401c8a1355c8847e153b   

                    Data_Projects_1                  Data_Projects_10  \
0  df057fc8cff04a9288074401848c32ab  5ecfc4503d2e46449076f8525edfe3d3   
1  24411e3197da4e9cb87868a13dacacfc  43ab0f71c1ec4b06ab329c437d2026b1   
2  5041ab3ecff84ec0befbacebb2a49c93  ad7fe8db1f8745faaa1a5942d2ebe28d   
3  23ade24b82fc453eb6ddc4955b087c9c  68f80fdb9f3045e99120e9d97c9892a3   
4  8fe3d7c6792b4da2b780581d95e452ca  33ef8522e5b44c53a8285a0d62eca470   

                   Data_Projects_11                  Data_Projects_12  \
0  ee05df8ac8ca48babc7191d5a2520106  fe51077e9f9e428e8408e3077a4641f3   
1  91f2b904d6e6432f93fe2f3a821fa92c  566a13dc7a2549b682cb4486c532eda7   
2  2e5580d5171241428a5b0dd6f9bf47f5  9defb57de89742bbbf432532c3b54187   
3  dd1e775595ab4159b8d3922b7e47b863  177dfe5e1e2c4a3ebc6671522df50478   
4  ef4bb062e9764df29c3d0f3262fdcb90  500f93b548d14d5aa4ae92b0523fea8a   

                   Data_Projects_13                  Data_Projects_14  \
0  694cf1575bb4429fa588aa5d34eed8c1  132e0edc21374d3581f2b8f303416f43   
1  8d9007e9b5774345baac3706571b8fff  a5c5204e226d4c1aa7dca5286350181d   
2  4cd95cfcba3545728dc84f2354c93757  ecf5b87b1ca64b1cbee99e72b3404876   
3  1463199409f34073b1da8ba4ab326987  986a63a22d174e59b984505f6ad017d1   
4  26b7276f6db6491a9a7546b2a417c5a5  5cf4bbeb3c084dcdad6e94789f12a1a4   

                   Data_Projects_15                  Data_Projects_16  \
0  d954f235460a42508ebcff3c1be4cff6  30a8d9e812534baa84bd4db4d660ae58   
1  4ba6a895fcda48829e6ccf3fa5edf602  8fc56726207e463ab0d54b657d12c5e3   
2  d9d9b87943694b849b8979d010d8c572  4562813379844b1cbaba785f7b587dff   
3  909ced564a634428b46df4bdc5779c37  d96ad2ce44df4069923bd1a549cb3ae5   
4  16e4c4ae52ad49cebfae54c06435d03b  519a6373cb9c4a0399e18048ded4b688   

                   Data_Projects_17                  Data_Projects_18  \
0  5cff6fb08cb44fbda6a82ed1d5390127  30f6eaef72064265b8f34584d7cfc08a   
1  82d4db1b9f114d239e31b8ab6243f6a0  b2a12ad58b4d40d5b3f24f99494fd999   
2  291b8f8b44504192834bdac694d1517b  a2035bca92df43a5a9a74259ca9039e1   
3  63eeb705714e4f9ba32c96c87cccb33e  eda6afd4d34f4f6d8fd18cba51a892f4   
4  a58e24e94d5d4fe7b5d84ffc95f835aa  afff88b4be354b6bb36ab5e7256a61b2   

                   Data_Projects_19                   Data_Projects_2  \
0  95a12a28310c43c099ca9d78b0c26c44  b4ad884f545d4885997751a58b0b342a   
1  3a55547fa5694af793327b6a5fac5fc6  24c7ea2602744c7a94cadf7f0c861dc7   
2  c5d62a4d0eeb4ad3bd7348dbff7bd6f2  61ccb4af7db84af0bc7cacc7650be164   
3  df5c981922854a02ad87a7508c4319d4  4ac5fcb835e241eab57b920b7d29c860   
4  218675151b734a7093bac8b875cbf4c5  541e931d73a94a99b760e833c8ddc057   

                   Data_Projects_20                  Data_Projects_21  \
0  324440f2fe1b42a0b07914b41590dddd  20db985c4e7f4a08bd2189554d91699f   
1  ac5e731cf83a4b6ca0d498b784d66b5b  2a329dc5a8314ed3b82cfed0a18740a8   
2  7a18dbdfd91644edbfab2c8a870f6eed  b4eaaf1e67e5441082fa0e3e99167ebd   
3  371ad5549dba4a758583a20cb0a45fbf  cfbc0d9f931941459a76f5bb0c7edc

In [897]:
# Calculate column groups
keywords = ['Data_ResourcesProducedFromStart_0_Count',	
            	'Data_ResourcesProducedFromStart_1_Count',	
            	'Data_ResourcesProducedFromStart_2_Count',	
                'Data_ResourcesProducedFromStart_3_Count',]
selected_cols, assetIds_cols, stringkey_cols, property_cols, misc_cols = select_columns(colonies_df, keywords)
colonies_df = colonies_df[selected_cols]

In [898]:
colonies_df[selected_cols]

AssetId  \
0  e433f1613297486cb6ddec834f37dd95   
1  883a5e2be9384e9f941ec3abf65f5d73   
2  876fc13fdc10492b8444e045ac8f9ecc   
3  0a8a3c9ea1b444118d33ebcc24db10f7   
4  47400e8140a3434882459f2c95b54b7f   

                                          Data_$type  \
0  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
1  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
2  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
3  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
4  aa1696d025c449f18968245aa30f56fd, BlueprintColony   

                    Data_Projects_0                   Data_Projects_1  \
0  bffe6bc0b8134433b1d724f472e7d72f  df057fc8cff04a9288074401848c32ab   
1  0e0dbf4dd52545ad82f58eba241bb61b  24411e3197da4e9cb87868a13dacacfc   
2  221c15362f084814b4937debf0757e94  5041ab3ecff84ec0befbacebb2a49c93   
3  b0243a87cbcc47ff894f104857016310  23ade24b82fc453eb6ddc4955b087c9c   
4  191508697446401c8a1355c8847e153b  8fe3d7c6792b4da2b780581d95e452ca   

                   Data_Projects_10                  Data_Projects_11  \
0  5ecfc4503d2e46449076f8525edfe3d3  ee05df8ac8ca48babc7191d5a2520106   
1  43ab0f71c1ec4b06ab329c437d2026b1  91f2b904d6e6432f93fe2f3a821fa92c   
2  ad7fe8db1f8745faaa1a5942d2ebe28d  2e5580d5171241428a5b0dd6f9bf47f5   
3  68f80fdb9f3045e99120e9d97c9892a3  dd1e775595ab4159b8d3922b7e47b863   
4  33ef8522e5b44c53a8285a0d62eca470  ef4bb062e9764df29c3d0f3262fdcb90   

                   Data_Projects_12                  Data_Projects_13  \
0  fe51077e9f9e428e8408e3077a4641f3  694cf1575bb4429fa588aa5d34eed8c1   
1  566a13dc7a2549b682cb4486c532eda7  8d9007e9b5774345baac3706571b8fff   
2  9defb57de89742bbbf432532c3b54187  4cd95cfcba3545728dc84f2354c93757   
3  177dfe5e1e2c4a3ebc6671522df50478  1463199409f34073b1da8ba4ab326987   
4  500f93b548d14d5aa4ae92b0523fea8a  26b7276f6db6491a9a7546b2a417c5a5   

                   Data_Projects_14                  Data_Projects_15  \
0  132e0edc21374d3581f2b8f303416f43  d954f235460a42508ebcff3c1be4cff6   
1  a5c5204e226d4c1aa7dca5286350181d  4ba6a895fcda48829e6ccf3fa5edf602   
2  ecf5b87b1ca64b1cbee99e72b3404876  d9d9b87943694b849b8979d010d8c572   
3  986a63a22d174e59b984505f6ad017d1  909ced564a634428b46df4bdc5779c37   
4  5cf4bbeb3c084dcdad6e94789f12a1a4  16e4c4ae52ad49cebfae54c06435d03b   

                   Data_Projects_16                  Data_Projects_17  \
0  30a8d9e812534baa84bd4db4d660ae58  5cff6fb08cb44fbda6a82ed1d5390127   
1  8fc56726207e463ab0d54b657d12c5e3  82d4db1b9f114d239e31b8ab6243f6a0   
2  4562813379844b1cbaba785f7b587dff  291b8f8b44504192834bdac694d1517b   
3  d96ad2ce44df4069923bd1a549cb3ae5  63eeb705714e4f9ba32c96c87cccb33e   
4  519a6373cb9c4a0399e18048ded4b688  a58e24e94d5d4fe7b5d84ffc95f835aa   

                   Data_Projects_18                  Data_Projects_19  \
0  30f6eaef72064265b8f34584d7cfc08a  95a12a28310c43c099ca9d78b0c26c44   
1  b2a12ad58b4d40d5b3f24f99494fd999  3a55547fa5694af793327b6a5fac5fc6   
2  a2035bca92df43a5a9a74259ca9039e1  c5d62a4d0eeb4ad3bd7348dbff7bd6f2   
3  eda6afd4d34f4f6d8fd18cba51a892f4  df5c981922854a02ad87a7508c4319d4   
4  afff88b4be354b6bb36ab5e7256a61b2  218675151b734a7093bac8b875cbf4c5   

                    Data_Projects_2                  Data_Projects_20  \
0  b4ad884f545d4885997751a58b0b342a  324440f2fe1b42a0b07914b41590dddd   
1  24c7ea2602744c7a94cadf7f0c861dc7  ac5e731cf83a4b6ca0d498b784d66b5b   
2  61ccb4af7db84af0bc7cacc7650be164  7a18dbdfd91644edbfab2c8a870f6eed   
3  4ac5fcb835e241eab57b920b7d29c860  371ad5549dba4a758583a20cb0a45fbf   
4  541e931d73a94a99b760e833c8ddc057  75edd8f1d5634c8a9b17b46d74680b55   

                   Data_Projects_21                  Data_Projects_22  \
0  20db985c4e7f4a08bd2189554d91699f  529f958459e1449cbb5754f5715e9903   
1  2a329dc5a8314ed3b82cfed0a18740a8  ef40908c8a7b4f858bb96f9d0c9e03b7   
2  b4eaaf1e67e5441082fa0e3e99167ebd  77d937b213464c70b106a4ef95f73f6d   
3  cfbc0d9f931941459a76f5bb0c7edc94  375268868d5f4a93bb47d7b52bfca10f   
4  5d7169363a064cc

In [899]:
#add planet name create_text_columns(df, index_df, columns_in, column_out, format_text=False):
colonies_df = create_text_columns(df = colonies_df,
                                  index_df = index_df,
                                  columns_in= stringkey_cols,
                                  column_out='Planet_Name')
selected_cols += ['Planet_Name']

In [900]:
colonies_df

AssetId  \
0  e433f1613297486cb6ddec834f37dd95   
1  883a5e2be9384e9f941ec3abf65f5d73   
2  876fc13fdc10492b8444e045ac8f9ecc   
3  0a8a3c9ea1b444118d33ebcc24db10f7   
4  47400e8140a3434882459f2c95b54b7f   

                                          Data_$type  \
0  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
1  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
2  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
3  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
4  aa1696d025c449f18968245aa30f56fd, BlueprintColony   

                    Data_Projects_0                   Data_Projects_1  \
0  bffe6bc0b8134433b1d724f472e7d72f  df057fc8cff04a9288074401848c32ab   
1  0e0dbf4dd52545ad82f58eba241bb61b  24411e3197da4e9cb87868a13dacacfc   
2  221c15362f084814b4937debf0757e94  5041ab3ecff84ec0befbacebb2a49c93   
3  b0243a87cbcc47ff894f104857016310  23ade24b82fc453eb6ddc4955b087c9c   
4  191508697446401c8a1355c8847e153b  8fe3d7c6792b4da2b780581d95e452ca   

                   Data_Projects_10                  Data_Projects_11  \
0  5ecfc4503d2e46449076f8525edfe3d3  ee05df8ac8ca48babc7191d5a2520106   
1  43ab0f71c1ec4b06ab329c437d2026b1  91f2b904d6e6432f93fe2f3a821fa92c   
2  ad7fe8db1f8745faaa1a5942d2ebe28d  2e5580d5171241428a5b0dd6f9bf47f5   
3  68f80fdb9f3045e99120e9d97c9892a3  dd1e775595ab4159b8d3922b7e47b863   
4  33ef8522e5b44c53a8285a0d62eca470  ef4bb062e9764df29c3d0f3262fdcb90   

                   Data_Projects_12                  Data_Projects_13  \
0  fe51077e9f9e428e8408e3077a4641f3  694cf1575bb4429fa588aa5d34eed8c1   
1  566a13dc7a2549b682cb4486c532eda7  8d9007e9b5774345baac3706571b8fff   
2  9defb57de89742bbbf432532c3b54187  4cd95cfcba3545728dc84f2354c93757   
3  177dfe5e1e2c4a3ebc6671522df50478  1463199409f34073b1da8ba4ab326987   
4  500f93b548d14d5aa4ae92b0523fea8a  26b7276f6db6491a9a7546b2a417c5a5   

                   Data_Projects_14                  Data_Projects_15  \
0  132e0edc21374d3581f2b8f303416f43  d954f235460a42508ebcff3c1be4cff6   
1  a5c5204e226d4c1aa7dca5286350181d  4ba6a895fcda48829e6ccf3fa5edf602   
2  ecf5b87b1ca64b1cbee99e72b3404876  d9d9b87943694b849b8979d010d8c572   
3  986a63a22d174e59b984505f6ad017d1  909ced564a634428b46df4bdc5779c37   
4  5cf4bbeb3c084dcdad6e94789f12a1a4  16e4c4ae52ad49cebfae54c06435d03b   

                   Data_Projects_16                  Data_Projects_17  \
0  30a8d9e812534baa84bd4db4d660ae58  5cff6fb08cb44fbda6a82ed1d5390127   
1  8fc56726207e463ab0d54b657d12c5e3  82d4db1b9f114d239e31b8ab6243f6a0   
2  4562813379844b1cbaba785f7b587dff  291b8f8b44504192834bdac694d1517b   
3  d96ad2ce44df4069923bd1a549cb3ae5  63eeb705714e4f9ba32c96c87cccb33e   
4  519a6373cb9c4a0399e18048ded4b688  a58e24e94d5d4fe7b5d84ffc95f835aa   

                   Data_Projects_18                  Data_Projects_19  \
0  30f6eaef72064265b8f34584d7cfc08a  95a12a28310c43c099ca9d78b0c26c44   
1  b2a12ad58b4d40d5b3f24f99494fd999  3a55547fa5694af793327b6a5fac5fc6   
2  a2035bca92df43a5a9a74259ca9039e1  c5d62a4d0eeb4ad3bd7348dbff7bd6f2   
3  eda6afd4d34f4f6d8fd18cba51a892f4  df5c981922854a02ad87a7508c4319d4   
4  afff88b4be354b6bb36ab5e7256a61b2  218675151b734a7093bac8b875cbf4c5   

                    Data_Projects_2                  Data_Projects_20  \
0  b4ad884f545d4885997751a58b0b342a  324440f2fe1b42a0b07914b41590dddd   
1  24c7ea2602744c7a94cadf7f0c861dc7  ac5e731cf83a4b6ca0d498b784d66b5b   
2  61ccb4af7db84af0bc7cacc7650be164  7a18dbdfd91644edbfab2c8a870f6eed   
3  4ac5fcb835e241eab57b920b7d29c860  371ad5549dba4a758583a20cb0a45fbf   
4  541e931d73a94a99b760e833c8ddc057  75edd8f1d5634c8a9b17b46d74680b55   

                   Data_Projects_21                  Data_Projects_22  \
0  20db985c4e7f4a08bd2189554d91699f  529f958459e1449cbb5754f5715e9903   
1  2a329dc5a8314ed3b82cfed0a18740a8  ef40908c8a7b4f858bb96f9d0c9e03b7   
2  b4eaaf1e67e5441082fa0e3e99167ebd  77d937b213464c70b106a4ef95f73f6d   
3  cfbc0d9f931941459a76f5bb0c7edc94  375268868d5f4a93bb47d7b52bfca10f   
4  5d7169363a064cc

# Dont delete
def get_text_info(df, map_df, index_df, columns_in, format_text=False, add_aggr_col = False):
    """ Function to create text columns with names and descriptions. Works on columns with asset ids
        and get filenames of those asset ids in asset_df and then look into files to extract strinkeys
        """
    # list of columns with string keys of items' names
    cols_names = columns_in
    #created column        
    # map_df - a dataframe for mapping    
    assets_dict = dict(zip(map_df.iloc[:,0],map_df.iloc[:,1])) #dict for mapping text information between two tables
    #reference to dataframe go from localization file    
    def find_stringkeys(row):    
        try:
            row = row.strip()
            with open(row) as asset_file:           
                file_contents = asset_file.read()
                data = json.loads(file_contents)
                try:
                    if data['Data']['m_Name']['Shared'] is not None:
                        key_list = [data['Data']['m_Name']['m_Key'], data['Data']['m_Name']['Shared']['stringkey']]
                        for key in key_list:                     
                            a = match_pattern(key) 
                            if a:                 
                                return key
                    else:
                        key = data['Data']['m_Name']['m_Key']
                        return key
                except Exception as err:
                    print(f'Unexpected {err=}, {type(err)=}',row)
                #print(data['Data']['m_DisplayName']['Shared'])
                
        except:
            return ''    
    
    #_____________________________Get items names and descriptions__________________________ 
    temp_list = []
    columns_out = []
    for col in cols_names:                
                df[col] = df[col].str.strip()         
                filenames_series = df[col].map(assets_dict)
                df['{}_stringkey'.format(col)]  = filenames_series.apply(find_stringkeys)
                temp_list.append('{}_stringkey'.format(col))
                text_column_name = '{}_text'.format(col)
                columns_out.append(text_column_name)   
    for i in range(len(columns_out)):
         col_in = [temp_list[i]]
         df = create_text_columns(df, index_df, col_in, columns_out[i], format_text = True)
    #drop created stringkey cols
    df = df.drop(columns = temp_list, axis = 1)
    if add_aggr_col == True:
        df['All_Items'] =df[columns_out].agg(sum)  
    return df, columns_out
    

In [901]:
#get_text_info(df, map_df, index_df, columns_in, format_text=False, add_aggr_col = False):
cols_in = assetIds_cols
colonies_df, created_cols = get_text_info(df = colonies_df,
                            map_df= assets_df, 
                            index_df = index_df,
                            columns_in=cols_in,
                            ) 

In [902]:
selected_cols += created_cols
colonies_df = colonies_df[selected_cols]
display(colonies_df)

AssetId  \
0  e433f1613297486cb6ddec834f37dd95   
1  883a5e2be9384e9f941ec3abf65f5d73   
2  876fc13fdc10492b8444e045ac8f9ecc   
3  0a8a3c9ea1b444118d33ebcc24db10f7   
4  47400e8140a3434882459f2c95b54b7f   

                                          Data_$type  \
0  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
1  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
2  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
3  aa1696d025c449f18968245aa30f56fd, BlueprintColony   
4  aa1696d025c449f18968245aa30f56fd, BlueprintColony   

                    Data_Projects_0                   Data_Projects_1  \
0  bffe6bc0b8134433b1d724f472e7d72f  df057fc8cff04a9288074401848c32ab   
1  0e0dbf4dd52545ad82f58eba241bb61b  24411e3197da4e9cb87868a13dacacfc   
2  221c15362f084814b4937debf0757e94  5041ab3ecff84ec0befbacebb2a49c93   
3  b0243a87cbcc47ff894f104857016310  23ade24b82fc453eb6ddc4955b087c9c   
4  191508697446401c8a1355c8847e153b  8fe3d7c6792b4da2b780581d95e452ca   

                   Data_Projects_10                  Data_Projects_11  \
0  5ecfc4503d2e46449076f8525edfe3d3  ee05df8ac8ca48babc7191d5a2520106   
1  43ab0f71c1ec4b06ab329c437d2026b1  91f2b904d6e6432f93fe2f3a821fa92c   
2  ad7fe8db1f8745faaa1a5942d2ebe28d  2e5580d5171241428a5b0dd6f9bf47f5   
3  68f80fdb9f3045e99120e9d97c9892a3  dd1e775595ab4159b8d3922b7e47b863   
4  33ef8522e5b44c53a8285a0d62eca470  ef4bb062e9764df29c3d0f3262fdcb90   

                   Data_Projects_12                  Data_Projects_13  \
0  fe51077e9f9e428e8408e3077a4641f3  694cf1575bb4429fa588aa5d34eed8c1   
1  566a13dc7a2549b682cb4486c532eda7  8d9007e9b5774345baac3706571b8fff   
2  9defb57de89742bbbf432532c3b54187  4cd95cfcba3545728dc84f2354c93757   
3  177dfe5e1e2c4a3ebc6671522df50478  1463199409f34073b1da8ba4ab326987   
4  500f93b548d14d5aa4ae92b0523fea8a  26b7276f6db6491a9a7546b2a417c5a5   

                   Data_Projects_14                  Data_Projects_15  \
0  132e0edc21374d3581f2b8f303416f43  d954f235460a42508ebcff3c1be4cff6   
1  a5c5204e226d4c1aa7dca5286350181d  4ba6a895fcda48829e6ccf3fa5edf602   
2  ecf5b87b1ca64b1cbee99e72b3404876  d9d9b87943694b849b8979d010d8c572   
3  986a63a22d174e59b984505f6ad017d1  909ced564a634428b46df4bdc5779c37   
4  5cf4bbeb3c084dcdad6e94789f12a1a4  16e4c4ae52ad49cebfae54c06435d03b   

                   Data_Projects_16                  Data_Projects_17  \
0  30a8d9e812534baa84bd4db4d660ae58  5cff6fb08cb44fbda6a82ed1d5390127   
1  8fc56726207e463ab0d54b657d12c5e3  82d4db1b9f114d239e31b8ab6243f6a0   
2  4562813379844b1cbaba785f7b587dff  291b8f8b44504192834bdac694d1517b   
3  d96ad2ce44df4069923bd1a549cb3ae5  63eeb705714e4f9ba32c96c87cccb33e   
4  519a6373cb9c4a0399e18048ded4b688  a58e24e94d5d4fe7b5d84ffc95f835aa   

                   Data_Projects_18                  Data_Projects_19  \
0  30f6eaef72064265b8f34584d7cfc08a  95a12a28310c43c099ca9d78b0c26c44   
1  b2a12ad58b4d40d5b3f24f99494fd999  3a55547fa5694af793327b6a5fac5fc6   
2  a2035bca92df43a5a9a74259ca9039e1  c5d62a4d0eeb4ad3bd7348dbff7bd6f2   
3  eda6afd4d34f4f6d8fd18cba51a892f4  df5c981922854a02ad87a7508c4319d4   
4  afff88b4be354b6bb36ab5e7256a61b2  218675151b734a7093bac8b875cbf4c5   

                    Data_Projects_2                  Data_Projects_20  \
0  b4ad884f545d4885997751a58b0b342a  324440f2fe1b42a0b07914b41590dddd   
1  24c7ea2602744c7a94cadf7f0c861dc7  ac5e731cf83a4b6ca0d498b784d66b5b   
2  61ccb4af7db84af0bc7cacc7650be164  7a18dbdfd91644edbfab2c8a870f6eed   
3  4ac5fcb835e241eab57b920b7d29c860  371ad5549dba4a758583a20cb0a45fbf   
4  541e931d73a94a99b760e833c8ddc057  75edd8f1d5634c8a9b17b46d74680b55   

                   Data_Projects_21                  Data_Projects_22  \
0  20db985c4e7f4a08bd2189554d91699f  529f958459e1449cbb5754f5715e9903   
1  2a329dc5a8314ed3b82cfed0a18740a8  ef40908c8a7b4f858bb96f9d0c9e03b7   
2  b4eaaf1e67e5441082fa0e3e99167ebd  77d937b213464c70b106a4ef95f73f6d   
3  cfbc0d9f931941459a76f5bb0c7edc94  375268868d5f4a93bb47d7b52bfca10f   
4  5d7169363a064cc

In [903]:
#Create aggregate column of available projects on each planet
target_cols = [x for x in created_cols if 'Data_Project' in x] # choose only columns with projects in newly created columns
colonies_df['All_Projects'] = colonies_df[target_cols].astype(str).agg(lambda x: ', '.join(word for word in x if word.strip()), axis = 1)
#display(colonies_df.head(1))

__________

### Colonization features table

**Notes**:  
Data types: features -  ```"cb208b98ceacca84baee15dba53b1979, BlueprintFeature"```  
            buffs - ```618a7e0d54149064ab3ffa5d9057362c, BlueprintBuff"```  

Folder: ```[Title](e:/Steam/RogueTrader/WorkFolder/Blueprints/GlobalMaps/Colonization/Rewards)```  
Names keys:  ```Data_m_DisplayName``` and ```Data_m_DisplayName_Shared_stringkey```.  
Descriptions keys: ```Data_m_Description_m_Key``` and ```Data_m_Description_Shared_stringkey```

If feature has a linked buff file, the assetid of it stored under 'Actions' keys.  
if buff file has a linked 'area eefect' asset id of it stored under ```m_AreaEffect``` key.  


In [904]:
features_df = colonization_data[colonization_data['Data_$type']=='cb208b98ceacca84baee15dba53b1979, BlueprintFeature'].reset_index(drop=True)
#Drop columns containing only nans, empty lists, empty dicts
features_df = drop_trash_columns(features_df)
#Drop unused columns
#colonies_df = colonies_df.drop(columns=['Data_Components','Data_Name_Shared_assetguid','Data_PlanetVisual'], axis = 1)
print(features_df.shape)
display(missing_values_tab(features_df))

(73, 507)
Dataframe contains 507 columns and 73 strings.

It has  500 columns with missed values


missed_values  %_of_all  \
Data_Components_1_BonusDeflectionValue_ValueRank                 72     98.63   
Data_Components_1_BonusAbsorptionValue_Property                  72     98.63   
Data_Components_3_Value_Getters_1_Value_ValueRank                72     98.63   
Data_Components_3_Value_Getters_1_Value_PropertyName             72     98.63   
Data_Components_3_Value_Getters_1_Value_Property                 72     98.63   
...                                                             ...       ...   
Data_Components_0_name                                            8     10.96   
Data_Components_0_$type                                           8     10.96   
Data_m_DisplayName_Shared_assetguid                               7      9.59   
Data_m_DisplayName_Shared_stringkey                               7      9.59   
Data_DlcType                                                      1      1.37   

                                                     data_type  
Data_Components_1_BonusDeflectionValue_ValueRank        object  
Data_Components_1_BonusAbsorptionValue_Property         object  
Data_Components_3_Value_Getters_1_Value_ValueRank       object  
Data_Components_3_Value_Getters_1_Value_PropertyName    object  
Data_Components_3_Value_Getters_1_Value_Property        object  
...                                                        ...  
Data_Components_0_name                                  object  
Data_Components_0_$type                                 object  
Data_m_DisplayName_Shared_assetguid                     object  
Data_m_DisplayName_Shared_stringkey                     object  
Data_DlcType                                            object  

[500 rows x 3 columns]

None

In [905]:
keywords = []
selected_cols, assetIds_cols, stringkey_cols, property_cols, misc_cols = select_columns(features_df, keywords)
features_df = features_df[selected_cols]

In [906]:
display(features_df.head())

AssetId  \
0  e34da1ba12d2499b9bd931a9833356c4   
1  cb18304edf9948d3ab617720ad0294e4   
2  6183fd3f845a44f8a773fbf400988852   
3  f65444e75cae4c958df2189ec217e0c8   
4  42153dd9c8464d9aa9319a32b83f1d12   

                                           Data_$type  \
0  cb208b98ceacca84baee15dba53b1979, BlueprintFeature   
1  cb208b98ceacca84baee15dba53b1979, BlueprintFeature   
2  cb208b98ceacca84baee15dba53b1979, BlueprintFeature   
3  cb208b98ceacca84baee15dba53b1979, BlueprintFeature   
4  cb208b98ceacca84baee15dba53b1979, BlueprintFeature   

  Data_Components_0_Activated_Actions_0_m_Buff  \
0                                          NaN   
1                                          NaN   
2                                          NaN   
3                                          NaN   
4                                          NaN   

  Data_Components_0_AdditionalDescription_Shared_assetguid  \
0                                                      NaN   
1                                                      NaN   
2                                                      NaN   
3                                                      NaN   
4                                                      NaN   

  Data_Components_0_Deactivated_Actions_0_m_Buff  \
0                                            NaN   
1                                            NaN   
2                                            NaN   
3                                            NaN   
4                                            NaN   

  Data_Components_0_Restrictions_Property_Getters_0_m_Fact  \
0                                                      NaN   
1                                                      NaN   
2                         e19237e1d5f1431ebdea633406d24653   
3                                                      NaN   
4                                                      NaN   

  Data_Components_0_Restrictions_Property_Getters_1_m_Fact  \
0                                                      NaN   
1                                                      NaN   
2                                                      NaN   
3                                                      NaN   
4                                                      NaN   

  Data_Components_0_Restrictions_Property_Getters_2_m_Fact  \
0                                                      NaN   
1                                                      NaN   
2                                                      NaN   
3                                                      NaN   
4                                                      NaN   

  Data_Components_0_Restrictions_Property_Getters_3_m_Fact  \
0                                                      NaN   
1                                                      NaN   
2                                                      NaN   
3                                                      NaN   
4                                                      NaN   

  Data_Components_1_Abilities_0 Data_Components_1_Abilities_1  \
0                           NaN                           NaN   
1                           NaN                           NaN   
2                           NaN                           NaN   
3                           NaN                           NaN   
4                           NaN                           NaN   

  Data_Components_1_Abilities_2 Data_Components_1_Abilities_3  \
0                           NaN                           NaN   
1                           NaN                           NaN   
2                           NaN                           NaN   
3                           NaN                           NaN   
4                           NaN                           NaN   

  Data_Components_1_Abilities_4 Data_Components_1_Abilities_5  \
0                           NaN                           NaN   
1                           NaN                           N

In [907]:
#add planet name create_text_columns(df, index_df, columns_in, column_out, format_text=False):
col_names = ['Data_m_DisplayName_Shared_stringkey','Data_m_DisplayName_m_Key']
col_descr = ['Data_m_Description_Shared_stringkey','Data_m_Description_m_Key']
#create name columns
features_df = create_text_columns(df = features_df,
                                  index_df = index_df,
                                  columns_in= col_names,
                                  column_out='Feature_Name')
#
features_df = create_text_columns(df = features_df,
                                  index_df = index_df,
                                  columns_in= col_descr,
                                  column_out='Feature_Descr')

In [908]:
features_df.head()

AssetId  \
0  e34da1ba12d2499b9bd931a9833356c4   
1  cb18304edf9948d3ab617720ad0294e4   
2  6183fd3f845a44f8a773fbf400988852   
3  f65444e75cae4c958df2189ec217e0c8   
4  42153dd9c8464d9aa9319a32b83f1d12   

                                           Data_$type  \
0  cb208b98ceacca84baee15dba53b1979, BlueprintFeature   
1  cb208b98ceacca84baee15dba53b1979, BlueprintFeature   
2  cb208b98ceacca84baee15dba53b1979, BlueprintFeature   
3  cb208b98ceacca84baee15dba53b1979, BlueprintFeature   
4  cb208b98ceacca84baee15dba53b1979, BlueprintFeature   

  Data_Components_0_Activated_Actions_0_m_Buff  \
0                                          NaN   
1                                          NaN   
2                                          NaN   
3                                          NaN   
4                                          NaN   

  Data_Components_0_AdditionalDescription_Shared_assetguid  \
0                                                      NaN   
1                                                      NaN   
2                                                      NaN   
3                                                      NaN   
4                                                      NaN   

  Data_Components_0_Deactivated_Actions_0_m_Buff  \
0                                            NaN   
1                                            NaN   
2                                            NaN   
3                                            NaN   
4                                            NaN   

  Data_Components_0_Restrictions_Property_Getters_0_m_Fact  \
0                                                      NaN   
1                                                      NaN   
2                         e19237e1d5f1431ebdea633406d24653   
3                                                      NaN   
4                                                      NaN   

  Data_Components_0_Restrictions_Property_Getters_1_m_Fact  \
0                                                      NaN   
1                                                      NaN   
2                                                      NaN   
3                                                      NaN   
4                                                      NaN   

  Data_Components_0_Restrictions_Property_Getters_2_m_Fact  \
0                                                      NaN   
1                                                      NaN   
2                                                      NaN   
3                                                      NaN   
4                                                      NaN   

  Data_Components_0_Restrictions_Property_Getters_3_m_Fact  \
0                                                      NaN   
1                                                      NaN   
2                                                      NaN   
3                                                      NaN   
4                                                      NaN   

  Data_Components_1_Abilities_0 Data_Components_1_Abilities_1  \
0                           NaN                           NaN   
1                           NaN                           NaN   
2                           NaN                           NaN   
3                           NaN                           NaN   
4                           NaN                           NaN   

  Data_Components_1_Abilities_2 Data_Components_1_Abilities_3  \
0                           NaN                           NaN   
1                           NaN                           NaN   
2                           NaN                           NaN   
3                           NaN                           NaN   
4                           NaN                           NaN   

  Data_Components_1_Abilities_4 Data_Components_1_Abilities_5  \
0                           NaN                           NaN   
1                           NaN                           N

In [909]:
stringkey_cols

['Data_Components_0_AdditionalDescription_Shared_stringkey',
 'Data_m_Description_Shared_stringkey',
 'Data_m_Description_m_Key',
 'Data_m_DisplayName_Shared_stringkey',
 'Data_m_DisplayName_m_Key']

_________

### Colonization rewards

________

f6713a6e3041461885cb61c97a6919f6

In [910]:
display(colonization_data[colonization_data['AssetId']=="f6713a6e3041461885cb61c97a6919f6"])

AssetId  \
1259  f6713a6e3041461885cb61c97a6919f6   

                                             Data_$type  \
1259  c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog   

      Data_AccessibilityModifier Data_ActionsOnFinish_Actions  \
1259                         NaN                          NaN   

     Data_ActionsOnFinish_Actions_0_$type  \
1259                                  NaN   

     Data_ActionsOnFinish_Actions_0_Etude  \
1259                                  NaN   

      Data_ActionsOnFinish_Actions_0_EtudeEvaluator  \
1259                                            NaN   

     Data_ActionsOnFinish_Actions_0_Evaluate  \
1259                                     NaN   

     Data_ActionsOnFinish_Actions_0_Trait  \
1259                                  NaN   

     Data_ActionsOnFinish_Actions_0_UnlockIfNot  \
1259                                        NaN   

     Data_ActionsOnFinish_Actions_0_Value_$type  \
1259                                        NaN   

      Data_ActionsOnFinish_Actions_0_Value_Value  \
1259                                         NaN   

     Data_ActionsOnFinish_Actions_0_Value_name  \
1259                                       NaN   

     Data_ActionsOnFinish_Actions_0_m_Chronicle  \
1259                                        NaN   

     Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint  \
1259                                              NaN   

     Data_ActionsOnFinish_Actions_0_m_Flag  \
1259                                   NaN   

     Data_ActionsOnFinish_Actions_0_name Data_ActionsOnFinish_Actions_1_$type  \
1259                                 NaN                                  NaN   

     Data_ActionsOnFinish_Actions_1_Etude  \
1259                                  NaN   

      Data_ActionsOnFinish_Actions_1_EtudeEvaluator  \
1259                                            NaN   

     Data_ActionsOnFinish_Actions_1_Evaluate  \
1259                                     NaN   

     Data_ActionsOnFinish_Actions_1_StartImmediately  \
1259                                             NaN   

     Data_ActionsOnFinish_Actions_1_m_Chronicle  \
1259                                        NaN   

     Data_ActionsOnFinish_Actions_1_m_ColonyBlueprint  \
1259                                              NaN   

     Data_ActionsOnFinish_Actions_1_m_NewVisualBlueprint  \
1259                                                 NaN   

     Data_ActionsOnFinish_Actions_1_m_Planet  \
1259                                     NaN   

      Data_ActionsOnFinish_Actions_1_m_ProductivityPercents  \
1259                                                    NaN   

     Data_ActionsOnFinish_Actions_1_name Data_ActionsOnFinish_Actions_2_$type  \
1259                                 NaN                                  NaN   

     Data_ActionsOnFinish_Actions_2_Etude  \
1259                                  NaN   

      Data_ActionsOnFinish_Actions_2_EtudeEvaluator  \
1259                                            NaN   

     Data_ActionsOnFinish_Actions_2_Evaluate  \
1259                                     NaN   

     Data_ActionsOnFinish_Actions_2_StartImmediately  \
1259                                             NaN   

     Data_ActionsOnFinish_Actions_2_name Data_ActionsOnFinish_Actions_3_$type  \
1259                                 NaN                                  NaN   

     Data_ActionsOnFinish_Actions_3_StartObjectiveIfNone  \
1259                                                 NaN   

     Data_ActionsOnFinish_Actions_3_Status  \
1259                                   NaN   

     Data_ActionsOnFinish_Actions_3_m_Objective  \
1259                                        NaN   

     Data_ActionsOnFinish_Actions_3_name Data_ActionsOnFinish_Actions_4_$type  \
1259                                 NaN                                  NaN   

     Data_ActionsOnFinish_Actions_4_m_Achievement  \
1259                                          NaN   

     Data_ActionsOnFinish_Act

### Strategical projects

#### Creation

In [911]:
#folder_projects = r'e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Projects\Strategical'
folder_projects = r'e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Projects'
skip_folder = ['Test']
list_of_files = []
for root,dirs,files in os.walk(folder_projects):
        dirs[:] = [x for x in dirs if x not in skip_folder ]
        for file in files:
            list_of_files.append(os.path.join(root, file))
projects_data = create_df(list_of_files)
#print(list_of_files)


In [912]:
#Drop columns containing only nans, empty lists, empty dicts
projects_data = drop_trash_columns(projects_data)
#print(context_cols)
print(projects_data.shape)
display(projects_data.head())


(159, 445)


AssetId  \
0  a13aeac5979c4237893268172c3caf5b   
1  291b8f8b44504192834bdac694d1517b   
2  a2035bca92df43a5a9a74259ca9039e1   
3  0defacc47e0d4968a6b6e6da5b3796c0   
4  df5c981922854a02ad87a7508c4319d4   

                                                 Data_$type  \
0  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   
1  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   
2  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   
3  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   
4  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   

              Data_ActionsOnFinish_Actions_0_$type  \
0  09697d9710264407a9c32060cfe8a2c7, CompleteEtude   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   

  Data_ActionsOnFinish_Actions_0_Etude Data_ActionsOnFinish_Actions_0_Trait  \
0     8c8d57ff636f4d9cbff599b9e1359f3f                                  NaN   
1                                  NaN                                  NaN   
2                                  NaN                                  NaN   
3                                  NaN                                  NaN   
4                                  NaN                                  NaN   

  Data_ActionsOnFinish_Actions_0_Value_$type  \
0                                        NaN   
1                                        NaN   
2                                        NaN   
3                                        NaN   
4                                        NaN   

  Data_ActionsOnFinish_Actions_0_Value_Value  \
0                                        NaN   
1                                        NaN   
2                                        NaN   
3                                        NaN   
4                                        NaN   

  Data_ActionsOnFinish_Actions_0_Value_name  \
0                                       NaN   
1                                       NaN   
2                                       NaN   
3                                       NaN   
4                                       NaN   

  Data_ActionsOnFinish_Actions_0_m_Chronicle  \
0                                        NaN   
1                                        NaN   
2                                        NaN   
3                                        NaN   
4                                        NaN   

  Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint  \
0                                              NaN   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   

  Data_ActionsOnFinish_Actions_0_m_Flag  \
0                                   NaN   
1                                   NaN   
2                                   NaN   
3                                   NaN   
4                                   NaN   

               Data_ActionsOnFinish_Actions_0_name  \
0  $CompleteEtude$d29583bab62d42f485c23efff9580599   
1                                              NaN   
2                                              NaN   
3                                              NaN   
4                                              NaN   

           Data_ActionsOnFinish_Actions_1_$type  \
0  6ab8dd2cc3ba43e8b76882f981bf2b99, StartEtude   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   

  Data_ActionsOnFinish_Actions_1_Etude  \
0     1b27a91797b74f98bb602b83ee557787   
1                                  NaN   
2                                  NaN   
3                                  NaN   
4                                  NaN

In [913]:
projects_data.query('AssetId=="9528e6903c6c481da440cf84c4336a2c"')

AssetId  \
52  9528e6903c6c481da440cf84c4336a2c   

                                                  Data_$type  \
52  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   

   Data_ActionsOnFinish_Actions_0_$type Data_ActionsOnFinish_Actions_0_Etude  \
52                                  NaN                                  NaN   

   Data_ActionsOnFinish_Actions_0_Trait  \
52                                  NaN   

   Data_ActionsOnFinish_Actions_0_Value_$type  \
52                                        NaN   

   Data_ActionsOnFinish_Actions_0_Value_Value  \
52                                        NaN   

   Data_ActionsOnFinish_Actions_0_Value_name  \
52                                       NaN   

   Data_ActionsOnFinish_Actions_0_m_Chronicle  \
52                                        NaN   

   Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint  \
52                                              NaN   

   Data_ActionsOnFinish_Actions_0_m_Flag Data_ActionsOnFinish_Actions_0_name  \
52                                   NaN                                 NaN   

   Data_ActionsOnFinish_Actions_1_$type Data_ActionsOnFinish_Actions_1_Etude  \
52                                  NaN                                  NaN   

   Data_ActionsOnFinish_Actions_1_m_Chronicle  \
52                                        NaN   

   Data_ActionsOnFinish_Actions_1_m_ColonyBlueprint  \
52                                              NaN   

   Data_ActionsOnFinish_Actions_1_m_NewVisualBlueprint  \
52                                                 NaN   

   Data_ActionsOnFinish_Actions_1_m_Planet  \
52                                     NaN   

   Data_ActionsOnFinish_Actions_1_m_ProductivityPercents  \
52                                                   NaN   

   Data_ActionsOnFinish_Actions_1_name Data_ActionsOnFinish_Actions_2_$type  \
52                                 NaN                                  NaN   

   Data_ActionsOnFinish_Actions_2_Etude Data_ActionsOnFinish_Actions_2_name  \
52                                  NaN                                 NaN   

   Data_ActionsOnFinish_Actions_3_$type Data_ActionsOnFinish_Actions_3_Status  \
52                                  NaN                                   NaN   

   Data_ActionsOnFinish_Actions_3_m_Objective  \
52                                        NaN   

   Data_ActionsOnFinish_Actions_3_name Data_ActionsOnFinish_Actions_4_$type  \
52                                 NaN                                  NaN   

   Data_ActionsOnFinish_Actions_4_m_Achievement  \
52                                          NaN   

   Data_ActionsOnFinish_Actions_4_name  \
52                                 NaN   

   Data_AvailabilityConditions_Conditions_0_$type  \
52                                            NaN   

   Data_AvailabilityConditions_Conditions_0_Playing  \
52                                              NaN   

   Data_AvailabilityConditions_Conditions_0_Started  \
52                                              NaN   

   Data_AvailabilityConditions_Conditions_0_Unit_$type  \
52                                                 NaN   

   Data_AvailabilityConditions_Conditions_0_Unit_name  \
52                                                NaN   

   Data_AvailabilityConditions_Conditions_0_m_Cue  \
52                                            NaN   

   Data_AvailabilityConditions_Conditions_0_m_Direction  \
52                                                  NaN   

   Data_AvailabilityConditions_Conditions_0_m_Etude  \
52                                              NaN   

   Data_AvailabilityConditions_Conditions_0_m_Fact  \
52                                             NaN   

   Data_AvailabilityConditions_Conditions_0_name  \
52                                           NaN   

   Data_AvailabilityConditions_Conditions_1_$type  \
52                                            NaN   

   Data_AvailabilityConditions_Conditions_1_NotStarted  \

#### Calculation of column groups

In [914]:
keywords = []
selected_cols, assetIds_cols, stringkey_cols, property_cols, misc_cols = select_columns(projects_data, keywords)
#resource name colums
res_cols = [x for x in projects_data.columns if 'Resource_Resource' in x]
#res count columns
res_count_cols = [x for x in projects_data.columns if 'Resource_Count' in x]
#print(res_count_cols)
print(len(res_count_cols), len(res_cols))

22 22


In [915]:
misc_cols = ['Data_ActionsOnFinish_Actions_0_Trait',
 'Data_ActionsOnFinish_Actions_0_m_Chronicle',
 'Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint',
 'Data_ActionsOnFinish_Actions_0_m_Flag',
 'Data_ActionsOnFinish_Actions_1_m_Chronicle',
 'Data_ActionsOnFinish_Actions_1_m_ColonyBlueprint',
 'Data_ActionsOnFinish_Actions_1_m_NewVisualBlueprint',
 'Data_ActionsOnFinish_Actions_1_m_Planet',
 'Data_ActionsOnFinish_Actions_2_Etude',
 'Data_ActionsOnFinish_Actions_3_m_Objective',
 'Data_ActionsOnFinish_Actions_4_m_Achievement',
 'Data_AvailabilityConditions_Conditions_0_m_Etude',]
etude_cols = [x for x in projects_data.columns if 'Etude' in x]

In [916]:
#convert count cols to int
projects_data[res_count_cols] = projects_data[res_count_cols].fillna(0)
projects_data[res_count_cols] = projects_data[res_count_cols].astype('int')
#fill missing values in stringley columns
projects_data[stringkey_cols] = projects_data[stringkey_cols].fillna('')

#### Add text information:

In [917]:
col_names = ['Data_m_Name_Shared_stringkey']
col_descr = ['Data_m_Description_Shared_stringkey']
#create name columns
projects_data = create_text_columns(df = projects_data,
                                  index_df = index_df,
                                  columns_in= col_names,
                                  column_out='Project_Name')
#
projects_data = create_text_columns(df = projects_data,
                                  index_df = index_df,
                                  columns_in= col_descr,
                                  column_out='Project_Descr')

#### Add resource names

In [918]:
#get_text_info(df, map_df, index_df, columns_in, format_text=False, add_aggr_col = False)
projects_data,created_cols = get_text_info(df= projects_data,
                              map_df = assets_df,
                              index_df = index_df,
                              columns_in = res_cols,
                              )
#find text information for other columns with ids
other_property_cols = [x for x in property_cols if '$type' not in x] 
projects_data,created_cols1 = get_text_info(df= projects_data,
                              map_df = assets_df,
                              index_df = index_df,
                              columns_in = other_property_cols,
                              )

In [919]:
projects_data[['AssetId', 'Project_Name'] + other_property_cols + created_cols1+ ['Filepath']].head()

AssetId                             Project_Name  \
0  a13aeac5979c4237893268172c3caf5b  Execution of the Heretic Vistenza Vyatt   
1  291b8f8b44504192834bdac694d1517b                         Dark Experiments   
2  a2035bca92df43a5a9a74259ca9039e1                       A Mechanical Trade   
3  0defacc47e0d4968a6b6e6da5b3796c0                         Lair in the Void   
4  df5c981922854a02ad87a7508c4319d4                               Navy Whips   

         Data_Components_0_m_Colony          Data_Components_0_m_Fact  \
0  47400e8140a3434882459f2c95b54b7f                               NaN   
1                               NaN  f806946e00504449a81ccabec0476b40   
2                               NaN                               NaN   
3                               NaN                               NaN   
4                               NaN                               NaN   

           Data_Components_0_m_Item Data_Components_0_m_NotBuiltProject  \
0                               NaN                                 NaN   
1                               NaN                                 NaN   
2  9c899527ffbd45c389a1e7e0f3437aa9                                 NaN   
3  82bec0310585476ca65f4f109557557c                                 NaN   
4  af978f6d159b464d9fd6cf71ce056993                                 NaN   

  Data_Components_0_m_Objective Data_Components_0_m_Unit  \
0                           NaN                      NaN   
1                           NaN                      NaN   
2                           NaN                      NaN   
3                           NaN                      NaN   
4                           NaN                      NaN   

  Data_Components_1_m_Cargo        Data_Components_1_m_Colony  \
0                       NaN  47400e8140a3434882459f2c95b54b7f   
1                       NaN                               NaN   
2                       NaN                               NaN   
3                       NaN                               NaN   
4                       NaN                               NaN   

  Data_Components_1_m_Fact          Data_Components_1_m_Item  \
0                      NaN                               NaN   
1                      NaN  57818d38b6924b6ba972af645664ecbb   
2                      NaN                               NaN   
3                      NaN  82bec0310585476ca65f4f109557557c   
4                      NaN                               NaN   

  Data_Components_1_m_NotBuiltProject Data_Components_1_m_Objective  \
0                                 NaN                           NaN   
1                                 NaN                           NaN   
2                                 NaN                           NaN   
3                                 NaN                           NaN   
4                                 NaN                           NaN   

  Data_Components_1_m_Projects_0 Data_Components_1_m_Projects_1  \
0                            NaN                            NaN   
1                            NaN                            NaN   
2                            NaN                            NaN   
3                            NaN                            NaN   
4                            NaN                            NaN   

  Data_Components_1_m_Projects_2 Data_Components_2_m_BuiltProject  \
0                            NaN                              NaN   
1                            NaN                              NaN   
2                            NaN                              NaN   
3                            NaN                              NaN   
4                            NaN                              NaN   

         Data_Components_2_m_Colony Data_Components_2_m_NotBuiltProject  \
0                               NaN                                 NaN   
1                               NaN                                 NaN   
2                               NaN               

#### Create aggregate columns:

In [920]:
def concat_column_values(df, columns, name):
    df[name] = df[columns].astype(str).agg(lambda x: ', '.join(word for word in x if word.strip()), axis = 1)
    return df

In [921]:
#list of columns with blocked projects
blocked_cols = [x for x in projects_data.columns if '_NotBuiltProject_text' in x ]
projects_data = concat_column_values(projects_data, blocked_cols,'Blocked_Projects')
# list of columns with prerequisite projects
required_projects = [x for x in projects_data.columns if '_BuiltProject_text' in x ]
projects_data = concat_column_values(projects_data, required_projects,'Required_Projects')

In [922]:
display(projects_data[['Project_Name'] + ['Blocked_Projects','Required_Projects']].head(10))

Project_Name  \
0  Execution of the Heretic Vistenza Vyatt   
1                         Dark Experiments   
2                       A Mechanical Trade   
3                         Lair in the Void   
4                               Navy Whips   
5                    The Science of Virtue   
6                             Sordid Goods   
7                      Kasballican Auction   
8                             Militia Navy   
9                          Maglev Railways   

                       Blocked_Projects Required_Projects  
0                                                          
1                    A Mechanical Trade                    
2                      Dark Experiments                    
3  Holy Servitude, Extractium Metallica                    
4                                                          
5                     Rose of Zamarkand                    
6                   Kasballican Auction                    
7                          Sordid Goods                    
8                                                          
9              Cemetery of the Faithful

In [923]:
projects_data.query('Required_Projects!=""')[['Project_Name'] + ['Blocked_Projects','Required_Projects']].head()

Project_Name                Blocked_Projects  \
52           The Reaping                                   
94               Bastion                                   
122              Crusade    In Drusus' Footsteps, Shrine   
123               Shrine   In Drusus' Footsteps, Crusade   
125  Mechanised Servants  Forest Fortresses, Xenodefence   

             Required_Projects  
52                      Giants  
94                Missionaries  
122  Bonfires of Righteousness  
123               Good Tidings  
125     Dark Sages, Dark Sages

#### Add planet name

In [924]:
# select columns with project names in colonies_df
project_cols = [x for x in colonies_df.columns if 'Project' in x if '_text' in x]
# select columns with projects ids in colonies_df
project_ids_cols = [x for x in colonies_df.columns if 'Data_Projects_' in x if '_text' not in x] 
print(project_ids_cols)
#make a copy from colonies df
projects_ids_df = colonies_df[['AssetId', 'Planet_Name'] + project_cols + project_ids_cols].copy(deep=True)
# transform it to long format
projects_ids_df = pd.melt(projects_ids_df,  id_vars=['Planet_Name'], value_vars= project_ids_cols)
#drop unused column
projects_ids_df = projects_ids_df.drop(columns=['variable'], axis = 1)

['Data_Projects_0', 'Data_Projects_1', 'Data_Projects_10', 'Data_Projects_11', 'Data_Projects_12', 'Data_Projects_13', 'Data_Projects_14', 'Data_Projects_15', 'Data_Projects_16', 'Data_Projects_17', 'Data_Projects_18', 'Data_Projects_19', 'Data_Projects_2', 'Data_Projects_20', 'Data_Projects_21', 'Data_Projects_22', 'Data_Projects_23', 'Data_Projects_3', 'Data_Projects_4', 'Data_Projects_5', 'Data_Projects_6', 'Data_Projects_7', 'Data_Projects_8', 'Data_Projects_9']


#### Merging ```projects_data``` with ```projects_ids_df``` on the columns with ids:

In [925]:
projects_data = projects_data.merge(projects_ids_df,
                                     how = 'left',
                                       left_on = ['AssetId'],
                                       right_on = ['value'],
                                       suffixes=('_x','_y')).drop(columns = ['value'])

In [926]:
projects_data[['AssetId','Planet_Name','Project_Name']].head()
display(projects_data.query('Planet_Name=="Janus"')[['AssetId','Planet_Name','Project_Name']].head())

AssetId Planet_Name  \
0   a13aeac5979c4237893268172c3caf5b       Janus   
5   d1bde03ac3ef404697479c5e6e4e9104       Janus   
13  218675151b734a7093bac8b875cbf4c5       Janus   
15  a58e24e94d5d4fe7b5d84ffc95f835aa       Janus   
26  91f57be7824d46c682a72f278c0556db       Janus   

                               Project_Name  
0   Execution of the Heretic Vistenza Vyatt  
5                     The Science of Virtue  
13                                 The Lost  
15                         Xenos Intoxicant  
26                         A Cure for Sloth

**Reaping**    
id:  9528e6903c6c481da440cf84c4336a2c   
stringkey:  4aff4201-0021-4730-be0f-731a3521f1bf

#### Add aggregate resource requirement columns:

In [927]:
def extract_num_from_string(name):
    """Function to extract number from string"""
    return int(''.join(filter(str.isdigit,name)))
# columns with resource names and quantities
cols_to_arrange = res_count_cols +created_cols

#### Create items table from projects_data

In [928]:
#columns with item ids
item_cols = [x for x in projects_data.columns if 'Item' in x]
#columns with project ranks
project_rank_cols = [x for x in projects_data.columns if 'Rank' in x]
print(item_cols)
projects_data['Data_Components_1_m_Item_text'].unique()

['Data_Components_0_m_Item', 'Data_Components_1_m_Item', 'Data_Components_0_m_Item_text', 'Data_Components_1_m_Item_text']


array(['', '"Fangs of Janus" Macro-Weapons', 'Iron-Eye Grenade',
       'Pollen of the Unreal', 'Crimson Haze', 'Hospitalant Medical Kit',
       'Chirurgeon Medikit', 'Scorcher', 'Frag Grenade Mk XVI',
       'Triumph and Fury', 'Tears of Repentance', 'Apexalium Stimulant'],
      dtype=object)

**Notes**:  
If item in the column '''Data_Components_1_m_Item_text''' (the number is not 0) it means it appears in the second from top cell on the left side of the planet project interface and usually it means that item is a ship equipment or consumable.

In [929]:
# Search for items that are in the right text column but not present in the left item text column
projects_data[(projects_data['Data_Components_0_m_Item_text']=='') 
              & (projects_data['Data_Components_1_m_Item_text']!='')][item_cols+ ['Planet_Name']]

Data_Components_0_m_Item          Data_Components_1_m_Item  \
1                        NaN  57818d38b6924b6ba972af645664ecbb   
144                      NaN  7ef8cb18b35044fda24270c838a73b1d   

    Data_Components_0_m_Item_text   Data_Components_1_m_Item_text  Planet_Name  
1                                  "Fangs of Janus" Macro-Weapons  Kiava Gamma  
144                                              Triumph and Fury  Kiava Gamma

Add items  '"Fangs of Janus" Macro-Weapons'	and 'Triumph and Fury' to column ```Data_Components_0_m_Item_text```:

In [930]:
projects_items = projects_data[['AssetId','Project_Name','Data_Rank', 'Planet_Name'] +item_cols].copy(deep=True)
projects_items.head()

AssetId                             Project_Name  \
0  a13aeac5979c4237893268172c3caf5b  Execution of the Heretic Vistenza Vyatt   
1  291b8f8b44504192834bdac694d1517b                         Dark Experiments   
2  a2035bca92df43a5a9a74259ca9039e1                       A Mechanical Trade   
3  0defacc47e0d4968a6b6e6da5b3796c0                         Lair in the Void   
4  df5c981922854a02ad87a7508c4319d4                               Navy Whips   

  Data_Rank  Planet_Name          Data_Components_0_m_Item  \
0    Second        Janus                               NaN   
1    Fourth  Kiava Gamma                               NaN   
2    Fourth  Kiava Gamma  9c899527ffbd45c389a1e7e0f3437aa9   
3    Second   Vheabos VI  82bec0310585476ca65f4f109557557c   
4    Fourth   Vheabos VI  af978f6d159b464d9fd6cf71ce056993   

           Data_Components_1_m_Item Data_Components_0_m_Item_text  \
0                               NaN                                 
1  57818d38b6924b6ba972af645664ecbb                                 
2                               NaN    Archeotech Repulsor Shield   
3  82bec0310585476ca65f4f109557557c              Iron-Eye Grenade   
4                               NaN                   Eviscerator   

    Data_Components_1_m_Item_text  
0                                  
1  "Fangs of Janus" Macro-Weapons  
2                                  
3                Iron-Eye Grenade  
4

In [931]:
projects_items['Item_Name'] = np.where(projects_items['Data_Components_0_m_Item_text']=="",
                                  projects_items['Data_Components_1_m_Item_text'],
                                   projects_items['Data_Components_0_m_Item_text'] )
projects_items['Item_AssetId'] = np.where(projects_items['Data_Components_0_m_Item'].isna(),
                                  projects_items['Data_Components_1_m_Item'],
                                   projects_items['Data_Components_0_m_Item'] )

In [932]:
# select only rows where item id is not nan to choose only project with items
projects_items = projects_items.query('Item_AssetId.notna()')[['AssetId','Planet_Name', 'Data_Rank', 'Project_Name',  'Item_Name','Item_AssetId']]
#rename column 'Data_Rank'
project_items = projects_items.rename(columns = {'Data_Rank':'Project_Rank'}, inplace=True)
projects_items.head(10)

AssetId  Planet_Name Project_Rank  \
1   291b8f8b44504192834bdac694d1517b  Kiava Gamma       Fourth   
2   a2035bca92df43a5a9a74259ca9039e1  Kiava Gamma       Fourth   
3   0defacc47e0d4968a6b6e6da5b3796c0   Vheabos VI       Second   
4   df5c981922854a02ad87a7508c4319d4   Vheabos VI       Fourth   
5   d1bde03ac3ef404697479c5e6e4e9104        Janus       Second   
6   8723f0032cbe43e7bc5aabc08c6a4417     Dargonus       Second   
7   64281bd7b40543209db1ee66b9dfe652     Dargonus       Second   
9   a8ffa7699b7a415197f191178eb3c694    Foulstone       Second   
11  d388cd262d9b4bd7a02747d73ca51a6d   Vheabos VI       Second   
12  eba769e652eb4aeeb9f1aeb9fbd91e1f   Vheabos VI       Second   

             Project_Name                       Item_Name  \
1        Dark Experiments  "Fangs of Janus" Macro-Weapons   
2      A Mechanical Trade      Archeotech Repulsor Shield   
3        Lair in the Void                Iron-Eye Grenade   
4              Navy Whips                     Eviscerator   
5   The Science of Virtue                 Eyes of Joyeuse   
6            Sordid Goods                          Zealot   
7     Kasballican Auction                The Ashen Breath   
9         Maglev Railways               Transonic Emitter   
11         Holy Servitude                       Vigilance   
12   Extractium Metallica               Mobile Extractium   

                        Item_AssetId  
1   57818d38b6924b6ba972af645664ecbb  
2   9c899527ffbd45c389a1e7e0f3437aa9  
3   82bec0310585476ca65f4f109557557c  
4   af978f6d159b464d9fd6cf71ce056993  
5   7f67bc4d7e1c4ef6b217b46e4f55bf0b  
6   58d255a12dd946129d166ee618687862  
7   ac81e67ac2874517b406c8008559a5a9  
9   d39b28ade6844440833698efa3d8e2a7  
11  9637aec54bc644949441f7e390c5abd6  
12  4ffaa1fe758f497ca90ae9301b37abaa

In [933]:
#make hard copy
projects_items_table = projects_items.copy(deep=True)

__________

### Get items from dialogs

#### Exploring links between parameters

**Notes**:  
Finding a link between ```projects_data``` and ```answers_data``` about project triggering dialogs after being completed which provides items if succeded skillchecks.  
Project Sky Barrier which provides item 'Cogni Simulator'.  
Etude id starting after completed projected: c6e79b068c9b4987875964a0fcd1561a    

"FinishActions": {
      "Actions": [
        {
          "$type": "727d31d013cf5d34eac20031d87ee75c, FinishChronicle",
          "name": "$FinishChronicle$4deedc8295084375ac782eed4d7345bf",
          "m_Chronicle": "!bp_738efcb576d748b69b781c6eff057c8f",
          "m_ColonyBlueprint": "!bp_876fc13fdc10492b8444e045ac8f9ecc"
        }
      ]
    },

  "!bp_1ebacc092c844ac296ea247d276e6d91",
      "!bp_9c88641fb70f4dd8969f075c8c4224f7",
      "!bp_101653fcfdb94e09b1fc169a145d067b",
      "!bp_413ffd88dd9548289cf181e43c2485a9"

In [934]:
display(projects_data.query('Project_Name=="Sky Barrier"'))

AssetId  \
144  b4eaaf1e67e5441082fa0e3e99167ebd   

                                                   Data_$type  \
144  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   

                 Data_ActionsOnFinish_Actions_0_$type  \
144  1fd3c7ebaa8a499d9e5f7ac9a43bf6af, StartChronicle   

    Data_ActionsOnFinish_Actions_0_Etude Data_ActionsOnFinish_Actions_0_Trait  \
144                                  NaN                                  NaN   

    Data_ActionsOnFinish_Actions_0_Value_$type  \
144                                        NaN   

    Data_ActionsOnFinish_Actions_0_Value_Value  \
144                                        NaN   

    Data_ActionsOnFinish_Actions_0_Value_name  \
144                                       NaN   

    Data_ActionsOnFinish_Actions_0_m_Chronicle  \
144           f6713a6e3041461885cb61c97a6919f6   

    Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint  \
144                 876fc13fdc10492b8444e045ac8f9ecc   

    Data_ActionsOnFinish_Actions_0_m_Flag  \
144                                   NaN   

                  Data_ActionsOnFinish_Actions_0_name  \
144  $StartChronicle$8207e6a28a9d4d4f932b205a9f046044   

                     Data_ActionsOnFinish_Actions_1_$type  \
144  7def417596434663b95228f37bc18af3, ChangePlanetVisual   

    Data_ActionsOnFinish_Actions_1_Etude  \
144                                  NaN   

    Data_ActionsOnFinish_Actions_1_m_Chronicle  \
144                                        NaN   

    Data_ActionsOnFinish_Actions_1_m_ColonyBlueprint  \
144                                              NaN   

    Data_ActionsOnFinish_Actions_1_m_NewVisualBlueprint  \
144                    dd0700cec34148cfafa03cfdb4a2a0b4   

    Data_ActionsOnFinish_Actions_1_m_Planet  \
144        4502e1f275ed4ac4a77805dd5bc02e7c   

    Data_ActionsOnFinish_Actions_1_m_ProductivityPercents  \
144                                                   NaN   

                          Data_ActionsOnFinish_Actions_1_name  \
144  $ChangePlanetVisual$bd8e8d56-2d88-45b3-8f24-2585b759995d   

             Data_ActionsOnFinish_Actions_2_$type  \
144  6ab8dd2cc3ba43e8b76882f981bf2b99, StartEtude   

    Data_ActionsOnFinish_Actions_2_Etude  \
144     c6e79b068c9b4987875964a0fcd1561a   

                  Data_ActionsOnFinish_Actions_2_name  \
144  $StartEtude$89d286ba-0975-4f3f-9977-1e8e1aeb9b63   

                     Data_ActionsOnFinish_Actions_3_$type  \
144  31abd123cda0b4147b509219dbb097a0, SetObjectiveStatus   

    Data_ActionsOnFinish_Actions_3_Status  \
144                              Complete   

    Data_ActionsOnFinish_Actions_3_m_Objective  \
144           2a472be2c646497983ab549bcf0429c5   

                          Data_ActionsOnFinish_Actions_3_name  \
144  $SetObjectiveStatus$6818b931-f061-4cad-8983-582a1e0851fb   

                                    Data_ActionsOnFinish_Actions_4_$type  \
144  986015feb8a90774aba3ad6838fadd4f, ActionAchievementIncrementCounter   

    Data_ActionsOnFinish_Actions_4_m_Achievement  \
144             0b793e013e8d4532a90d7151c4cb2146   

                                     Data_ActionsOnFinish_Actions_4_name  \
144  $ActionAchievementIncrementCounter$62c5e08318224be68b3649ae7ab60533   

    Data_AvailabilityConditions_Conditions_0_$type  \
144  ea981728db8a5f84888ecba390671a05, EtudeStatus   

    Data_AvailabilityConditions_Conditions_0_Playing  \
144                                             True   

    Data_AvailabilityConditions_Conditions_0_Started  \
144                                            False   

    Data_AvailabilityConditions_Conditions_0_Unit_$type  \
144                                                 NaN   

    Data_AvailabilityConditions_Conditions_0_Unit_name  \
144                                                NaN   

    Data_AvailabilityConditions_Conditions_0_m_Cue  \
144                                            NaN   

    Data_AvailabilityConditions_Conditions_0_m_Direction  \
144            

In [935]:
display(projects_data.query('Project_Name=="Sky Barrier"'))

AssetId  \
144  b4eaaf1e67e5441082fa0e3e99167ebd   

                                                   Data_$type  \
144  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   

                 Data_ActionsOnFinish_Actions_0_$type  \
144  1fd3c7ebaa8a499d9e5f7ac9a43bf6af, StartChronicle   

    Data_ActionsOnFinish_Actions_0_Etude Data_ActionsOnFinish_Actions_0_Trait  \
144                                  NaN                                  NaN   

    Data_ActionsOnFinish_Actions_0_Value_$type  \
144                                        NaN   

    Data_ActionsOnFinish_Actions_0_Value_Value  \
144                                        NaN   

    Data_ActionsOnFinish_Actions_0_Value_name  \
144                                       NaN   

    Data_ActionsOnFinish_Actions_0_m_Chronicle  \
144           f6713a6e3041461885cb61c97a6919f6   

    Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint  \
144                 876fc13fdc10492b8444e045ac8f9ecc   

    Data_ActionsOnFinish_Actions_0_m_Flag  \
144                                   NaN   

                  Data_ActionsOnFinish_Actions_0_name  \
144  $StartChronicle$8207e6a28a9d4d4f932b205a9f046044   

                     Data_ActionsOnFinish_Actions_1_$type  \
144  7def417596434663b95228f37bc18af3, ChangePlanetVisual   

    Data_ActionsOnFinish_Actions_1_Etude  \
144                                  NaN   

    Data_ActionsOnFinish_Actions_1_m_Chronicle  \
144                                        NaN   

    Data_ActionsOnFinish_Actions_1_m_ColonyBlueprint  \
144                                              NaN   

    Data_ActionsOnFinish_Actions_1_m_NewVisualBlueprint  \
144                    dd0700cec34148cfafa03cfdb4a2a0b4   

    Data_ActionsOnFinish_Actions_1_m_Planet  \
144        4502e1f275ed4ac4a77805dd5bc02e7c   

    Data_ActionsOnFinish_Actions_1_m_ProductivityPercents  \
144                                                   NaN   

                          Data_ActionsOnFinish_Actions_1_name  \
144  $ChangePlanetVisual$bd8e8d56-2d88-45b3-8f24-2585b759995d   

             Data_ActionsOnFinish_Actions_2_$type  \
144  6ab8dd2cc3ba43e8b76882f981bf2b99, StartEtude   

    Data_ActionsOnFinish_Actions_2_Etude  \
144     c6e79b068c9b4987875964a0fcd1561a   

                  Data_ActionsOnFinish_Actions_2_name  \
144  $StartEtude$89d286ba-0975-4f3f-9977-1e8e1aeb9b63   

                     Data_ActionsOnFinish_Actions_3_$type  \
144  31abd123cda0b4147b509219dbb097a0, SetObjectiveStatus   

    Data_ActionsOnFinish_Actions_3_Status  \
144                              Complete   

    Data_ActionsOnFinish_Actions_3_m_Objective  \
144           2a472be2c646497983ab549bcf0429c5   

                          Data_ActionsOnFinish_Actions_3_name  \
144  $SetObjectiveStatus$6818b931-f061-4cad-8983-582a1e0851fb   

                                    Data_ActionsOnFinish_Actions_4_$type  \
144  986015feb8a90774aba3ad6838fadd4f, ActionAchievementIncrementCounter   

    Data_ActionsOnFinish_Actions_4_m_Achievement  \
144             0b793e013e8d4532a90d7151c4cb2146   

                                     Data_ActionsOnFinish_Actions_4_name  \
144  $ActionAchievementIncrementCounter$62c5e08318224be68b3649ae7ab60533   

    Data_AvailabilityConditions_Conditions_0_$type  \
144  ea981728db8a5f84888ecba390671a05, EtudeStatus   

    Data_AvailabilityConditions_Conditions_0_Playing  \
144                                             True   

    Data_AvailabilityConditions_Conditions_0_Started  \
144                                            False   

    Data_AvailabilityConditions_Conditions_0_Unit_$type  \
144                                                 NaN   

    Data_AvailabilityConditions_Conditions_0_Unit_name  \
144                                                NaN   

    Data_AvailabilityConditions_Conditions_0_m_Cue  \
144                                            NaN   

    Data_AvailabilityConditions_Conditions_0_m_Direction  \
144            

In [936]:
# find rows with Sky Barrier project id in the whole colonization table
colonization_data[colonization_data.eq("b4eaaf1e67e5441082fa0e3e99167ebd").any(axis = 1)]

AssetId  \
51    876fc13fdc10492b8444e045ac8f9ecc   
2346  b4eaaf1e67e5441082fa0e3e99167ebd   
2347  77d937b213464c70b106a4ef95f73f6d   
2348  669c01b39e234640b8d40ffc7aad72b1   

                                                    Data_$type  \
51           aa1696d025c449f18968245aa30f56fd, BlueprintColony   
2346  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   
2347  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   
2348  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   

      Data_AccessibilityModifier Data_ActionsOnFinish_Actions  \
51                           NaN                          NaN   
2346                         NaN                          NaN   
2347                         NaN                          NaN   
2348                         NaN                          NaN   

                  Data_ActionsOnFinish_Actions_0_$type  \
51                                                 NaN   
2346  1fd3c7ebaa8a499d9e5f7ac9a43bf6af, StartChronicle   
2347  1fd3c7ebaa8a499d9e5f7ac9a43bf6af, StartChronicle   
2348  1fd3c7ebaa8a499d9e5f7ac9a43bf6af, StartChronicle   

     Data_ActionsOnFinish_Actions_0_Etude  \
51                                    NaN   
2346                                  NaN   
2347                                  NaN   
2348                                  NaN   

      Data_ActionsOnFinish_Actions_0_EtudeEvaluator  \
51                                              NaN   
2346                                            NaN   
2347                                            NaN   
2348                                            NaN   

     Data_ActionsOnFinish_Actions_0_Evaluate  \
51                                       NaN   
2346                                     NaN   
2347                                     NaN   
2348                                     NaN   

     Data_ActionsOnFinish_Actions_0_Trait  \
51                                    NaN   
2346                                  NaN   
2347                                  NaN   
2348                                  NaN   

     Data_ActionsOnFinish_Actions_0_UnlockIfNot  \
51                                          NaN   
2346                                        NaN   
2347                                        NaN   
2348                                        NaN   

     Data_ActionsOnFinish_Actions_0_Value_$type  \
51                                          NaN   
2346                                        NaN   
2347                                        NaN   
2348                                        NaN   

      Data_ActionsOnFinish_Actions_0_Value_Value  \
51                                           NaN   
2346                                         NaN   
2347                                         NaN   
2348                                         NaN   

     Data_ActionsOnFinish_Actions_0_Value_name  \
51                                         NaN   
2346                                       NaN   
2347                                       NaN   
2348                                       NaN   

     Data_ActionsOnFinish_Actions_0_m_Chronicle  \
51                                          NaN   
2346           f6713a6e3041461885cb61c97a6919f6   
2347           f6713a6e3041461885cb61c97a6919f6   
2348           f6713a6e3041461885cb61c97a6919f6   

     Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint  \
51                                                NaN   
2346                 876fc13fdc10492b8444e045ac8f9ecc   
2347                 876fc13fdc10492b8444e045ac8f9ecc   
2348                 876fc13fdc10492b8444e045ac8f9ecc   

     Data_ActionsOnFinish_Actions_0_m_Flag  \
51                                     NaN   
2346                                   NaN   
2347                                   NaN   
2348                                   NaN   

                       Data_ActionsOnFinish_Actions_0_name  \
51                                          

Task: Find chronicle id =  f6713a6e3041461885cb61c97a6919f6	etude id = c6e79b068c9b4987875964a0fcd1561a, objective = 2a472be2c646497983ab549bcf0429c5 in derivatives of answers_data received from parsing its asset id columns. If found we can merge two tables via intermediary table.
Answer: go to answers_data ```Data_ParentAsset``` id file -> 'ParentAsset' id-> next file's 'ParentAsset' id

In [937]:
#search file with Data_ActionsOnFinish_Actions_0_m_Chronicle id:
print(assets_df.query('AssetId=="f6713a6e3041461885cb61c97a6919f6"')['File'])
# search [Data][FirstCue][Cues] id da1aaa22e5ee43349a40640e8f4be013
print(assets_df.query('AssetId=="da1aaa22e5ee43349a40640e8f4be013"')['File'])
# search [Data][Continue][Cues] id
print(assets_df.query('AssetId=="dc3f2d41e4c94a5d99d38772f0023331"')['File'])
# search [Data][Answers] id af45d35c667146f1889a1734b795ed65 to get assetid of answerlist file
print(assets_df.query('AssetId=="af45d35c667146f1889a1734b795ed65"')['File'])


8698    e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\KiavaGamma\KiavaGamma_Part_5_true\KiavaGamma_Part_5_dialogue_true.jbp
Name: File, dtype: object
8640    e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\KiavaGamma\KiavaGamma_Part_5_true\Cue_0001.jbp
Name: File, dtype: object
8677    e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\KiavaGamma\KiavaGamma_Part_5_true\Cue_2.jbp
Name: File, dtype: object
8600    e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\KiavaGamma\KiavaGamma_Part_5_true\AnswersList_0002.jbp
Name: File, dtype: object


**Notes**: the last id is equal to the id in the ```Data_ParentAsset``` column of the ```cogni_data```

In [938]:
#search StartActions Etude key:
assets_df.query('AssetId=="f4cc8c8a8b3d44e7ad3497a54d0296ab"')['File']

104784    e:\Steam\RogueTrader\WorkFolder\Blueprints\World\Etudes\RogueTraderEtude\Chapter02_Extra\MysteriousFunction_Searched.jbp
Name: File, dtype: object

In [939]:
# search parent key in mysterious function 43df2bda79bdbd0429fe2ca3064341b1
assets_df.query('AssetId=="b279344456df49eb8c8bdaf5742579a4"')['File']

104156    e:\Steam\RogueTrader\WorkFolder\Blueprints\World\Etudes\RogueTraderEtude\Chapter04_Extra.jbp
Name: File, dtype: object

Search from ```cogni_data``` side

In [940]:
# Check 'Data_ParentAsset'id field  af45d35c667146f1889a1734b795ed65	
print(assets_df.query('AssetId=="af45d35c667146f1889a1734b795ed65"')['File'])
# Check 'ParentAsset'id field  of the upper file
print(assets_df.query('AssetId=="dc3f2d41e4c94a5d99d38772f0023331"')['File'])
# Check 'ParentAsset'id field da1aaa22e5ee43349a40640e8f4be013 of the upper file
print(assets_df.query('AssetId=="da1aaa22e5ee43349a40640e8f4be013"')['File'])
# Check 'ParentAsset'id field  of the upper file
print(assets_df.query('AssetId=="f6713a6e3041461885cb61c97a6919f6"')['File'])

8600    e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\KiavaGamma\KiavaGamma_Part_5_true\AnswersList_0002.jbp
Name: File, dtype: object
8677    e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\KiavaGamma\KiavaGamma_Part_5_true\Cue_2.jbp
Name: File, dtype: object
8640    e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\KiavaGamma\KiavaGamma_Part_5_true\Cue_0001.jbp
Name: File, dtype: object
8698    e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\KiavaGamma\KiavaGamma_Part_5_true\KiavaGamma_Part_5_dialogue_true.jbp
Name: File, dtype: object


**Notes**: the last id is equal to the id in the column 'Data_ActionsOnFinish_Actions_0_m_Chronicle' of the ```sky_barrier_data```

#### Creation of dialog system summary table

In [941]:
# list of types of data responisoble for project chronicles
type_list = ["c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog", 
             "8eee9d45ddcfa614d99610c1892993e3, BlueprintCue",   
            "52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList",
            'df78945bb9f434e40b897758499cb714, BlueprintAnswer',
            'ab803aaa7a173f84e9172870c15e7493, BlueprintCheck',
            '72b026d82361459581a0cb453c0385cb, BlueprintColonyChronicle',
              ]
dialogs_data = colonization_data[colonization_data['Data_$type'].isin(type_list)].reset_index(drop = True)
#replace empty lists with nans
dialogs_data = dialogs_data.replace('[]',np.nan)
dialogs_data = drop_trash_columns(dialogs_data)
display(dialogs_data.head(5))
print(dialogs_data.shape)


AssetId  \
0  7326cd8552094a37b0ada5754a5d1816   
1  4068cab8ec99418d905301cc9b803060   
2  08f07a9a15ab49888f8679f2ece63aba   
3  12317ce8b1044d0984c70c4a06a160b3   
4  f5fdf9f8c2eb4acd97bff670b6c4ef49   

                                               Data_$type Data_AddToHistory  \
0  52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList               NaN   
1       df78945bb9f434e40b897758499cb714, BlueprintAnswer              True   
2       df78945bb9f434e40b897758499cb714, BlueprintAnswer              True   
3       df78945bb9f434e40b897758499cb714, BlueprintAnswer              True   
4       df78945bb9f434e40b897758499cb714, BlueprintAnswer              True   

  Data_AlignmentRequirement Data_AlignmentShift_Direction Data_Animation  \
0                       NaN                           NaN            NaN   
1                       NaN                           NaN            NaN   
2                       NaN                           NaN            NaN   
3                       NaN                           NaN            NaN   
4                       NaN                           NaN            NaN   

                     Data_Answers_0                    Data_Answers_1  \
0  4068cab8ec99418d905301cc9b803060  a0d948be8d94456ba4d59066c2608e80   
1                               NaN                               NaN   
2                               NaN                               NaN   
3                               NaN                               NaN   
4                               NaN                               NaN   

  Data_Answers_10 Data_Answers_11                    Data_Answers_2  \
0             NaN             NaN  8b0daca6abc240ccaaa97d2eb93444e8   
1             NaN             NaN                               NaN   
2             NaN             NaN                               NaN   
3             NaN             NaN                               NaN   
4             NaN             NaN                               NaN   

                     Data_Answers_3                    Data_Answers_4  \
0  08f07a9a15ab49888f8679f2ece63aba  beefd62b39b642e4b6c3f4f08ba515bc   
1                               NaN                               NaN   
2                               NaN                               NaN   
3                               NaN                               NaN   
4                               NaN                               NaN   

                     Data_Answers_5                    Data_Answers_6  \
0  12317ce8b1044d0984c70c4a06a160b3  3ef55abc14194780aca3a7752cd9f015   
1                               NaN                               NaN   
2                               NaN                               NaN   
3                               NaN                               NaN   
4                               NaN                               NaN   

                     Data_Answers_7 Data_Answers_8 Data_Answers_9  \
0  f5fdf9f8c2eb4acd97bff670b6c4ef49            NaN            NaN   
1                               NaN            NaN            NaN   
2                               NaN            NaN            NaN   
3                               NaN            NaN            NaN   
4                               NaN            NaN            NaN   

  Data_CharacterSelection_SelectionType  \
0                                   NaN   
1                                 Clear   
2                                 Clear   
3                                 Clear   
4                                 Clear   

                                         Data_Components_0_$type  \
0                                                            NaN   
1                                                            NaN   
2  2a09d956d9324196867de1714fc59e1e, RewardChangeStatContentment   
3   2aa503c54af44bd5b74037ea4f833dfb, RewardChangeStatEfficiency   
4             cb27cbda91354399b9c6f462df7ef378, RewardAddFeature   

  Data_Components_0_Faction  Data_

(1839, 447)


#### Create table of items, received from dialogs

In [942]:
#columns with item ids
item_columns = [x for x in dialogs_data.columns if 'Item' in x]
# columns with colony values
colony_columns = [x for x in dialogs_data.columns if 'Colony' in x ]
#columns with cue values
cues_cols = [x for x in dialogs_data.columns if 'Cue' in x]
#parent asset columns
parent_cols = [x for x in dialogs_data.columns if 'ParentAsset' in x]
# check what data types containing items
dialogs_data[dialogs_data[item_columns].notna().any(axis = 1)]['Data_$type'].unique()
#dataframe with item columns not na
dialog_items = (dialogs_data[dialogs_data[item_columns].notna().any(axis = 1)]
[['AssetId'] +  item_columns + colony_columns + cues_cols+parent_cols+ ['Filepath']]
).reset_index(drop = True)
dialog_items = drop_trash_columns(dialog_items)

In [943]:
#order columns
columns = ['AssetId', 'Data_Components_0_m_Item',
            'Data_Components_0_m_Colony',
             'Data_Components_1_m_Item',
             'Data_Components_1_m_Colony', 
            'Data_Components_2_m_Item', 
            'Data_Components_2_m_Colony',
            'Data_Components_3_m_Item',
            'Data_OnShow_Actions_0_m_ItemToGive',
       'Data_OnSelect_Actions_0_m_Colony',
       'Data_OnStop_Actions_0_m_ItemToGive',        
       'Data_OnSelect_Actions_1_m_Colony',
       'Data_OnShow_Actions_1_m_Colony',
        'Data_OnStop_Actions_1_m_Colony',
       'Data_Continue_Cues_0',
        'Data_NextCue_Cues_0',
        'Data_NextCue_Cues_1',
       'Data_NextCue_Cues_2',       
       'Data_ShowConditions_Conditions_0_m_Cue',
       'Data_ShowConditions_Conditions_1_m_Cue',
       'Data_ParentAsset',
        'Filepath']
dialog_items = dialog_items[columns]

Adding text information for colony columns:

In [944]:
columns = ['Data_Components_0_m_Colony', 'Data_Components_1_m_Colony', 'Data_Components_2_m_Colony']
dialog_items, created_columns = get_text_info(df = dialog_items,
                             map_df= assets_df,
                             index_df=index_df,
                             columns_in=columns)
dialog_items['All_Planets'] = dialog_items[created_columns].astype(str).agg(lambda x: ', '.join(word for word in x if word.strip()), axis = 1)
# Format column to split string into words
def split_strings(row):
    temp = row.split(',')
    return temp[0]
dialog_items['Planet_Name'] = dialog_items['All_Planets'].apply(split_strings)
#drop redundant column
dialog_items = dialog_items.drop(columns = ['All_Planets'])

Adding text information for item columns:

In [945]:
columns = ['Data_Components_0_m_Item', 'Data_Components_1_m_Item', 'Data_Components_2_m_Item', 'Data_Components_3_m_Item',
           'Data_OnShow_Actions_0_m_ItemToGive', 'Data_OnStop_Actions_0_m_ItemToGive']
dialog_items, created_columns = get_text_info(df = dialog_items,
                             map_df= assets_df,
                             index_df=index_df,
                             columns_in=columns)
dialog_items['Item_Name'] = dialog_items[created_columns].astype(str).agg(lambda x: ', '.join(word for word in x if word.strip()), axis = 1)
dialog_items['All_AssetId'] = dialog_items[columns].astype(str).agg(lambda x: ', '.join(word for word in x if word.strip()), axis = 1)
#function to extract 32key id from string
def extract_item_id(row):
        if None:
                return row
        else:
                row = re.search('[a-zA-Z0-9]{32}', str(row))
                return row[0]    
        
dialog_items['Item_AssetId'] = dialog_items['All_AssetId'].apply(extract_item_id)

#### Create tables of dialog sybsystems:

In [946]:
chronicles_df = dialogs_data[dialogs_data['Data_$type']=="72b026d82361459581a0cb453c0385cb, BlueprintColonyChronicle"]
chronicles_df = drop_trash_columns(chronicles_df)
print('Chronicles_df'.center(20))
display(chronicles_df.head())

#Creating table with  Data_$type=='c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog':
dialogs_df = dialogs_data[dialogs_data['Data_$type']=="c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog"]
#select target columns
columns = ['AssetId','Data_Conditions_Conditions_0_m_Colony', 'Data_FinishActions_Actions_0_m_ColonyBlueprint',
            'Data_FirstCue_Cues_0','Filepath']
dialogs_df = dialogs_df[columns]
dialogs_df = drop_trash_columns(dialogs_df)
print('Dialogs_df'.center(20))
display(dialogs_df.head())

#Create cues df
cues_df = dialogs_data[dialogs_data['Data_$type']=="8eee9d45ddcfa614d99610c1892993e3, BlueprintCue"]
columns = [x for x in cues_df.columns if 'ParentAsset' in x or  'Cue' in x or 'Answer' in x  ]
cues_df = cues_df[['AssetId'] + columns + ['Filepath']]
cues_df = drop_trash_columns(cues_df)
print('Cues_df'.center(20))
display(cues_df.head())

#Create df with Data_$type=="52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList"
answer_lists_df = dialogs_data[dialogs_data['Data_$type']=="52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList"]
answer_lists_df = drop_trash_columns(answer_lists_df)
print('AnswerLists'.center(20))
display(answer_lists_df.head())

   Chronicles_df    


AssetId  \
35   d1de65f37fc64aa78484f1023d734dcf   
75   b5968802fe0a4dcf82773009d10172b8   
113  27f7cebf0eb346afa9d635f5a135a7b4   
150  65e58f202b6d420bbbab24b3185a77db   
252  5f9cd4235eb94258b7663e545a97090e   

                                                     Data_$type  \
35   72b026d82361459581a0cb453c0385cb, BlueprintColonyChronicle   
75   72b026d82361459581a0cb453c0385cb, BlueprintColonyChronicle   
113  72b026d82361459581a0cb453c0385cb, BlueprintColonyChronicle   
150  72b026d82361459581a0cb453c0385cb, BlueprintColonyChronicle   
252  72b026d82361459581a0cb453c0385cb, BlueprintColonyChronicle   

               Data_m_BlueprintDialog  \
35   d5e49c0bbd67405a8c8aaa22bb9cfcf7   
75   06fb6b96d1ca4611b28b4c94283029f3   
113  28270a72320f4a6591a3715abb610fb0   
150  59fd079d48b34b449af0f8fbf1074e89   
252  f899fe78721d408bb35105cbc2197e6f   

                                                                                                                                                              Filepath  
35   e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Dargonus_Part_1_Chronicle.jbp  
75   e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_2\Dargonus_Part_2_Chronicle.jbp  
113  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_3\Dargonus_Part_3_Chronicle.jbp  
150  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_4\Dargonus_Part_4_Chronicle.jbp  
252  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_5\Dargonus_Part_5_Chronicle.jbp

     Dialogs_df     


AssetId Data_Conditions_Conditions_0_m_Colony  \
34   d5e49c0bbd67405a8c8aaa22bb9cfcf7                                   NaN   
74   06fb6b96d1ca4611b28b4c94283029f3                                   NaN   
112  28270a72320f4a6591a3715abb610fb0                                   NaN   
149  59fd079d48b34b449af0f8fbf1074e89                                   NaN   
251  f899fe78721d408bb35105cbc2197e6f                                   NaN   

    Data_FinishActions_Actions_0_m_ColonyBlueprint  \
34                e433f1613297486cb6ddec834f37dd95   
74                e433f1613297486cb6ddec834f37dd95   
112               e433f1613297486cb6ddec834f37dd95   
149               e433f1613297486cb6ddec834f37dd95   
251               e433f1613297486cb6ddec834f37dd95   

                 Data_FirstCue_Cues_0  \
34   5b088d2f604541cabab01b0f30aeb836   
74   477725480cdf42b69e038733f105391e   
112  de50d46474e045019c75849b9b50c034   
149  d9c0067c6b4a40f793d935018f75be49   
251  45f36b828f3f44fda84561896cd93a81   

                                                                                                                                                    Filepath  
34   e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Dargonus_Part_1.jbp  
74   e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_2\Dargonus_Part_2.jbp  
112  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_3\Dargonus_Part_3.jbp  
149  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_4\Dargonus_Part_4.jbp  
251  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_5\Dargonus_Part_5.jbp

      Cues_df       


AssetId                    Data_Answers_0  \
9   5b088d2f604541cabab01b0f30aeb836  7326cd8552094a37b0ada5754a5d1816   
10  ab5d213f67a44088afbd16be1a010bb1  7326cd8552094a37b0ada5754a5d1816   
11  c0a439da574e48d7804ce4427a138e09                               NaN   
12  68b38f32cfdc42d6a0dff65030b2a8a7                               NaN   
13  e1a1abbf7fe7495c847783c1867cec75                               NaN   

   Data_Conditions_Conditions_0_m_Answer Data_Conditions_Conditions_0_m_Cue  \
9                                    NaN                                NaN   
10                                   NaN                                NaN   
11                                   NaN                                NaN   
12                                   NaN                                NaN   
13                                   NaN                                NaN   

   Data_Continue_Cues_0 Data_Continue_Cues_1 Data_Continue_Cues_2  \
9                   NaN                  NaN                  NaN   
10                  NaN                  NaN                  NaN   
11                  NaN                  NaN                  NaN   
12                  NaN                  NaN                  NaN   
13                  NaN                  NaN                  NaN   

                    Data_ParentAsset  \
9   d5e49c0bbd67405a8c8aaa22bb9cfcf7   
10  4068cab8ec99418d905301cc9b803060   
11  5b088d2f604541cabab01b0f30aeb836   
12                               NaN   
13                               NaN   

                                                                                                                                            Filepath  
9   e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Cue_0001.jbp  
10  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Cue_0002.jbp  
11  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Cue_0003.jbp  
12  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Cue_0006.jbp  
13  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Cue_0007.jbp

    AnswerLists     


AssetId  \
0    7326cd8552094a37b0ada5754a5d1816   
36   093ae79c7e9046e38aae60128f8f83de   
76   7c46c72e02f64ffb9fd248791fd9b02b   
114  8a1b1a01af9f437b88472f4457d1ea0f   
151  3ea02262d53f4d4da44134e15b2b5976   

                                                 Data_$type  \
0    52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList   
36   52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList   
76   52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList   
114  52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList   
151  52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList   

    Data_AlignmentRequirement                    Data_Answers_0  \
0                         NaN  4068cab8ec99418d905301cc9b803060   
36                        NaN  b4e5b8932b814482ad7aa37f5be98dec   
76                        NaN  7bb14d1981594d3daa84225c993ce409   
114                       NaN  33cae5d538ca4f0d886ab0092cd78d54   
151                       NaN  5c2c12ab5fb4408ca23c73271ab0194a   

                       Data_Answers_1 Data_Answers_10 Data_Answers_11  \
0    a0d948be8d94456ba4d59066c2608e80             NaN             NaN   
36   b25c32a7784c46efa76db2337b327a46             NaN             NaN   
76   b36077fd301c4c02a3eddd70066e18c9             NaN             NaN   
114  e911ddf985264b41811e42253e41cbfd             NaN             NaN   
151  545471d129684007a90716e140408e06             NaN             NaN   

                       Data_Answers_2                    Data_Answers_3  \
0    8b0daca6abc240ccaaa97d2eb93444e8  08f07a9a15ab49888f8679f2ece63aba   
36   ded4379ce18c4fcc856025ae40a1e84c  1f20217bc203421b8314e1b61c07f54a   
76   1299398af2b74895a59c5ff62b4e8332  b5b1d2945ed4483baaa87b0c15357c5b   
114  decb61867a484afa9ef12e1bd4fdfcb1  444c7009ff6f4e5581e4ac4d716a651a   
151  e0ea48bbd8444d7b8e280f652b343d31  3ed46fab88664a4493a85c2cbd30dc17   

                       Data_Answers_4                    Data_Answers_5  \
0    beefd62b39b642e4b6c3f4f08ba515bc  12317ce8b1044d0984c70c4a06a160b3   
36   f9511e44854c402eaa120c21ff01c4df  eba0ac4eb7fb4b9e8da1a6905cd4e6ed   
76   9e2408928c72448c95f70edf1c0cf9f9  d18489e1a44b446c8d0ab2535203e9b0   
114  b3123323163c40f5957c4533b3cb8a43  7500194cffa24290a39b1529ba462f63   
151  2adacc9d1d184327924eb52f2a2b90b6  8f1c43cc4bf44d138403518478a5cdc9   

                       Data_Answers_6                    Data_Answers_7  \
0    3ef55abc14194780aca3a7752cd9f015  f5fdf9f8c2eb4acd97bff670b6c4ef49   
36   a662fd86a25e467185f7f2c73f103f66  2e86c423435642baa975d0af07df95e2   
76   2306c70b2e734f1d936a668c36705b3c  d391406566e9428f937ee47890a78a98   
114  1c2823d8525246f1a48d3f2227a6d73f                               NaN   
151                               NaN                               NaN   

                       Data_Answers_8 Data_Answers_9  \
0                                 NaN            NaN   
36   817f65c979094863a0073c013708e7f3            NaN   
76   4d94270503954a29b9f979508eb13ef2            NaN   
114                               NaN            NaN   
151                               NaN            NaN   

    Data_Conditions_Operation                  Data_ParentAsset  \
0                         And  5b088d2f604541cabab01b0f30aeb836   
36                        And  9852af25b58542adad20a4dc09641fc4   
76                        And  de50d46474e045019c75849b9b50c034   
114                       And  b7559d334f4c427c90dd1cf76a00b0ee   
151                       And  45f36b828f3f44fda84561896cd93a81   

    Data_SoulMarkRequirement_Direction  \
0                                 None   
36                                None   
76                                None   
114                               None   
151                               None   

                                                                                                                                                     Filepath  
0    e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMa

In [947]:
print('Unique chronicles in projects data: ',
    projects_data[
        projects_data['Data_ActionsOnFinish_Actions_0_m_Chronicle'].isin(chronicles_df['Data_m_BlueprintDialog'])]
        ['Data_ActionsOnFinish_Actions_0_m_Chronicle'].unique().shape[0]
        )
print('Unique chronicles total: ', chronicles_df['Data_m_BlueprintDialog'].unique().shape[0])


Unique chronicles in projects data:  23
Unique chronicles total:  25


Cues_df:

#### Merging

Algorithm of merging: 
1. Merge ```chronicles_df``` with dialogs_df, left_on = ```Data_m_BlueprintDialog``` , right_on = ```AssetId```  
2.  Merge ```dialogs_df``` with ```cues_df```, left_on = ```Data_FirstCue_Cues_0```, right_on = 'AssetId'.    
3. Merge with ```answerlist_df``` left_on = ```Data_Answers_0```, right_on = ```AssetId```.   
4. merge with ```dialog_items``` left_on = ```Data_Answers_0```, right_on = ```Data_ParentAsset```.  
5. Merge with ```projects_data``` left_on = ```Data_m_BlueprintDialog```, right_on = ```Data_ActionsOnFinish_Actions_0_m_Chronicle```.

In [948]:
# merge dialogs and chronicles
dialogs_merged = chronicles_df[['AssetId', 'Data_m_BlueprintDialog', 'Filepath']].merge(dialogs_df, left_on = ['Data_m_BlueprintDialog'],
                          right_on = ['AssetId'], how = 'right',
                          suffixes=('_chroniclesDF','_dialogsDF'))
#merge with cues table
dialogs_merged = dialogs_merged.merge(cues_df,
                                       how = 'right',
                                         left_on = 'Data_FirstCue_Cues_0',
                                           right_on = 'AssetId', suffixes = ('_dialogsDF','_cuesDF'))
#merge with answerlist
dialogs_merged = (dialogs_merged.merge(answer_lists_df[['AssetId','Data_ParentAsset','Filepath']], left_on = ['Data_Answers_0'],
                 right_on = ['AssetId'], how = 'left', suffixes=(None,'_answlistDF'))
                 ).rename(columns = {'AssetId':'AssetId_answlistDF','Filepath':'Filepath_answlistDF'}).reset_index(drop = True)
# merge with dialog_items
dialogs_merged = dialogs_merged.merge(dialog_items, how = 'right',
                                      left_on = ['Data_Answers_0'], 
                                      right_on = ['Data_ParentAsset'],
                                      suffixes = (None, '_itemsDF')).reset_index(drop = True)


In [949]:
display(dialogs_merged.head(1))

AssetId_chroniclesDF Data_m_BlueprintDialog Filepath_chroniclesDF  \
0                  NaN                    NaN                   NaN   

  AssetId_dialogsDF Data_Conditions_Conditions_0_m_Colony  \
0               NaN                                   NaN   

  Data_FinishActions_Actions_0_m_ColonyBlueprint Data_FirstCue_Cues_0  \
0                                            NaN                  NaN   

  Filepath_dialogsDF                AssetId_answlistDF  \
0                NaN  9852af25b58542adad20a4dc09641fc4   

                     Data_Answers_0 Data_Conditions_Conditions_0_m_Answer  \
0  093ae79c7e9046e38aae60128f8f83de                                   NaN   

  Data_Conditions_Conditions_0_m_Cue Data_Continue_Cues_0  \
0                                NaN                  NaN   

  Data_Continue_Cues_1 Data_Continue_Cues_2                  Data_ParentAsset  \
0                  NaN                  NaN  9ca227e56df445ebb0731925dd8b52ea   

                                                                                                                                Filepath_answlistDF  \
0  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_2\Cue_0014.jbp   

                 AssetId_answlistDF       Data_ParentAsset_answlistDF  \
0  093ae79c7e9046e38aae60128f8f83de  9852af25b58542adad20a4dc09641fc4   

                                                                                                                                        Filepath_answlistDF  \
0  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_2\AnswersList_0002.jbp   

                            AssetId          Data_Components_0_m_Item  \
0  f9511e44854c402eaa120c21ff01c4df  2612a899accd40faa1639661c2a1b7f0   

  Data_Components_0_m_Colony Data_Components_1_m_Item  \
0                        NaN                      NaN   

  Data_Components_1_m_Colony Data_Components_2_m_Item  \
0                        NaN                      NaN   

         Data_Components_2_m_Colony Data_Components_3_m_Item  \
0  e433f1613297486cb6ddec834f37dd95                      NaN   

  Data_OnShow_Actions_0_m_ItemToGive  Data_OnSelect_Actions_0_m_Colony  \
0                                NaN  e433f1613297486cb6ddec834f37dd95   

  Data_OnStop_Actions_0_m_ItemToGive Data_OnSelect_Actions_1_m_Colony  \
0                                NaN                              NaN   

  Data_OnShow_Actions_1_m_Colony Data_OnStop_Actions_1_m_Colony  \
0                            NaN                            NaN   

  Data_Continue_Cues_0_itemsDF               Data_NextCue_Cues_0  \
0                          NaN  31e2bc4a55044814a41050ff8675921d   

  Data_NextCue_Cues_1 Data_NextCue_Cues_2  \
0                 NaN                 NaN   

  Data_ShowConditions_Conditions_0_m_Cue  \
0       acc7ae738272417c924564403cd40fd4   

  Data_ShowConditions_Conditions_1_m_Cue          Data_ParentAsset_itemsDF  \
0                                    NaN  093ae79c7e9046e38aae60128f8f83de   

                                                                                                                                              Filepath  \
0  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_2\Answer_0003.jbp   

  Data_Components_0_m_Colony_text Data_Components_1_m_Colony_text  \
0                                                                   

  Data_Components_2_m_Colony_text Planet_Name  \
0                        Dargonus    Dargonus   

                                                                                                                                                                                                         Data_Components_0_m_Item_text  \
0  This ancient component of a Dargonus-fleet frigate was discovered i

In [950]:
print('The number of rows in dialogs_merged',dialogs_merged.shape[0])
print('The number of answer list unique ids in merged table ',
      answer_lists_df[answer_lists_df['AssetId'].isin(dialogs_merged['Data_Answers_0'])].shape[0])
print('The number of unique items before merge', len(dialog_items['Item_Name'].unique()))
print('The number of unique items after merge', len(dialogs_merged['Item_Name'].unique()))

#check how many values exists in projects_data column 
display(dialogs_merged[dialogs_merged['Data_m_BlueprintDialog'].isin(projects_data['Data_ActionsOnFinish_Actions_0_m_Chronicle'])].shape[0])
print('Numeber of unique dialogs', len(dialogs_merged['Data_m_BlueprintDialog'].unique()))
display(dialogs_merged[dialogs_merged['AssetId_chroniclesDF'].isin(projects_data['Data_ActionsOnFinish_Actions_0_m_Chronicle'])].shape[0])

The number of rows in dialogs_merged 146
The number of answer list unique ids in merged table  20
The number of unique items before merge 33
The number of unique items after merge 33


144

Numeber of unique dialogs 8


122

Merge with projects_data:

Check distribution of merging keys:

print(dialogs_merged['Data_m_BlueprintDialog'].value_counts().sort_values(ascending=False))
print(projects_data['Data_ActionsOnFinish_Actions_0_m_Chronicle'].value_counts().sort_values(ascending=False))

Information about project ```Forbidden Planet``` on the planet Janus:

In [951]:
projects_data.query('Project_Name=="Forbidden Planet"')

AssetId  \
142  a012ad99267f45d1a18bfaea1a54af16   

                                                   Data_$type  \
142  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   

                 Data_ActionsOnFinish_Actions_0_$type  \
142  1fd3c7ebaa8a499d9e5f7ac9a43bf6af, StartChronicle   

    Data_ActionsOnFinish_Actions_0_Etude Data_ActionsOnFinish_Actions_0_Trait  \
142                                  NaN                                  NaN   

    Data_ActionsOnFinish_Actions_0_Value_$type  \
142                                        NaN   

    Data_ActionsOnFinish_Actions_0_Value_Value  \
142                                        NaN   

    Data_ActionsOnFinish_Actions_0_Value_name  \
142                                       NaN   

    Data_ActionsOnFinish_Actions_0_m_Chronicle  \
142           25a86da04d1d43a6b7da07180cd51cf7   

    Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint  \
142                 47400e8140a3434882459f2c95b54b7f   

    Data_ActionsOnFinish_Actions_0_m_Flag  \
142                                   NaN   

                      Data_ActionsOnFinish_Actions_0_name  \
142  $StartChronicle$ebccb60f-836e-4780-868a-31c024492330   

                     Data_ActionsOnFinish_Actions_1_$type  \
142  7def417596434663b95228f37bc18af3, ChangePlanetVisual   

    Data_ActionsOnFinish_Actions_1_Etude  \
142                                  NaN   

    Data_ActionsOnFinish_Actions_1_m_Chronicle  \
142                                        NaN   

    Data_ActionsOnFinish_Actions_1_m_ColonyBlueprint  \
142                                              NaN   

    Data_ActionsOnFinish_Actions_1_m_NewVisualBlueprint  \
142                    1f90a050c3d646a198a7968c3988007b   

    Data_ActionsOnFinish_Actions_1_m_Planet  \
142        055bc9cdac5e4f8eae0307b97d4b8d8f   

    Data_ActionsOnFinish_Actions_1_m_ProductivityPercents  \
142                                                   NaN   

                          Data_ActionsOnFinish_Actions_1_name  \
142  $ChangePlanetVisual$debeb125-469e-470e-8611-659500b18f8b   

             Data_ActionsOnFinish_Actions_2_$type  \
142  6ab8dd2cc3ba43e8b76882f981bf2b99, StartEtude   

    Data_ActionsOnFinish_Actions_2_Etude  \
142     c6e79b068c9b4987875964a0fcd1561a   

                  Data_ActionsOnFinish_Actions_2_name  \
142  $StartEtude$e720d030-e03c-41c9-9e54-64465bd4f7aa   

                     Data_ActionsOnFinish_Actions_3_$type  \
142  31abd123cda0b4147b509219dbb097a0, SetObjectiveStatus   

    Data_ActionsOnFinish_Actions_3_Status  \
142                              Complete   

    Data_ActionsOnFinish_Actions_3_m_Objective  \
142           2a472be2c646497983ab549bcf0429c5   

                          Data_ActionsOnFinish_Actions_3_name  \
142  $SetObjectiveStatus$992d100c-ef31-474e-9171-b18cd5b8dbb2   

                                    Data_ActionsOnFinish_Actions_4_$type  \
142  986015feb8a90774aba3ad6838fadd4f, ActionAchievementIncrementCounter   

    Data_ActionsOnFinish_Actions_4_m_Achievement  \
142             0b793e013e8d4532a90d7151c4cb2146   

                                     Data_ActionsOnFinish_Actions_4_name  \
142  $ActionAchievementIncrementCounter$166e1e852a8648c998a8dafe75bc72aa   

    Data_AvailabilityConditions_Conditions_0_$type  \
142  ea981728db8a5f84888ecba390671a05, EtudeStatus   

    Data_AvailabilityConditions_Conditions_0_Playing  \
142                                             True   

    Data_AvailabilityConditions_Conditions_0_Started  \
142                                            False   

    Data_AvailabilityConditions_Conditions_0_Unit_$type  \
142                                                 NaN   

    Data_AvailabilityConditions_Conditions_0_Unit_name  \
142                                                NaN   

    Data_AvailabilityConditions_Conditions_0_m_Cue  \
142                                            NaN   

    Data_AvailabilityConditions_Conditions_0_m_Direction  \
142    

In [952]:
print('Dialogs_merged'.center(20))
display(dialogs_merged[dialogs_merged.eq("Lilaethan's Fury").any(axis = 1)])
print('Dialog_items'.center(20))
display(dialog_items[dialog_items.eq("Lilaethan's Fury").any(axis = 1)])
print('Projects_data'.center(20))
display(projects_data[projects_data.eq("5a6c467ef0e5464f82b173a056bab794").any(axis = 1)])   

   Dialogs_merged   


AssetId_chroniclesDF Data_m_BlueprintDialog Filepath_chroniclesDF  \
114                  NaN                    NaN                   NaN   

    AssetId_dialogsDF Data_Conditions_Conditions_0_m_Colony  \
114               NaN                                   NaN   

    Data_FinishActions_Actions_0_m_ColonyBlueprint Data_FirstCue_Cues_0  \
114                                            NaN                  NaN   

    Filepath_dialogsDF AssetId_answlistDF Data_Answers_0  \
114                NaN                NaN            NaN   

    Data_Conditions_Conditions_0_m_Answer Data_Conditions_Conditions_0_m_Cue  \
114                                   NaN                                NaN   

    Data_Continue_Cues_0 Data_Continue_Cues_1 Data_Continue_Cues_2  \
114                  NaN                  NaN                  NaN   

    Data_ParentAsset Filepath_answlistDF AssetId_answlistDF  \
114              NaN                 NaN                NaN   

    Data_ParentAsset_answlistDF Filepath_answlistDF  \
114                         NaN                 NaN   

                              AssetId Data_Components_0_m_Item  \
114  6867f88dadab49dd903015320ad6bc82                      NaN   

    Data_Components_0_m_Colony Data_Components_1_m_Item  \
114                        NaN                      NaN   

    Data_Components_1_m_Colony Data_Components_2_m_Item  \
114                        NaN                      NaN   

    Data_Components_2_m_Colony Data_Components_3_m_Item  \
114                        NaN                      NaN   

    Data_OnShow_Actions_0_m_ItemToGive Data_OnSelect_Actions_0_m_Colony  \
114                                NaN                              NaN   

    Data_OnStop_Actions_0_m_ItemToGive Data_OnSelect_Actions_1_m_Colony  \
114   1ca7c664e50c4ba39b55b294d5765d84                              NaN   

    Data_OnShow_Actions_1_m_Colony    Data_OnStop_Actions_1_m_Colony  \
114                            NaN  47400e8140a3434882459f2c95b54b7f   

         Data_Continue_Cues_0_itemsDF Data_NextCue_Cues_0 Data_NextCue_Cues_1  \
114  5a6c467ef0e5464f82b173a056bab794                 NaN                 NaN   

    Data_NextCue_Cues_2 Data_ShowConditions_Conditions_0_m_Cue  \
114                 NaN                                    NaN   

    Data_ShowConditions_Conditions_1_m_Cue          Data_ParentAsset_itemsDF  \
114                                    NaN  cef24515739145df8a543b8725384f48   

                                                                                                                                       Filepath  \
114  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Janus\Janus_Part_5\Cue_0045.jbp   

    Data_Components_0_m_Colony_text Data_Components_1_m_Colony_text  \
114                                                                   

    Data_Components_2_m_Colony_text Planet_Name Data_Components_0_m_Item_text  \
114                                                                             

    Data_Components_1_m_Item_text Data_Components_2_m_Item_text  \
114                                                               

    Data_Components_3_m_Item_text Data_OnShow_Actions_0_m_ItemToGive_text  \
114                                                                         

    Data_OnStop_Actions_0_m_ItemToGive_text         Item_Name  \
114                        Lilaethan's Fury  Lilaethan's Fury   

                                                   All_AssetId  \
114  nan, nan, nan, nan, nan, 1ca7c664e50c4ba39b55b294d5765d84   

                         Item_AssetId  
114  1ca7c664e50c4ba39b55b294d5765d84

    Dialog_items    


AssetId Data_Components_0_m_Item  \
41  6867f88dadab49dd903015320ad6bc82                      NaN   

   Data_Components_0_m_Colony Data_Components_1_m_Item  \
41                        NaN                      NaN   

   Data_Components_1_m_Colony Data_Components_2_m_Item  \
41                        NaN                      NaN   

   Data_Components_2_m_Colony Data_Components_3_m_Item  \
41                        NaN                      NaN   

   Data_OnShow_Actions_0_m_ItemToGive Data_OnSelect_Actions_0_m_Colony  \
41                                NaN                              NaN   

   Data_OnStop_Actions_0_m_ItemToGive Data_OnSelect_Actions_1_m_Colony  \
41   1ca7c664e50c4ba39b55b294d5765d84                              NaN   

   Data_OnShow_Actions_1_m_Colony    Data_OnStop_Actions_1_m_Colony  \
41                            NaN  47400e8140a3434882459f2c95b54b7f   

                Data_Continue_Cues_0 Data_NextCue_Cues_0 Data_NextCue_Cues_1  \
41  5a6c467ef0e5464f82b173a056bab794                 NaN                 NaN   

   Data_NextCue_Cues_2 Data_ShowConditions_Conditions_0_m_Cue  \
41                 NaN                                    NaN   

   Data_ShowConditions_Conditions_1_m_Cue                  Data_ParentAsset  \
41                                    NaN  cef24515739145df8a543b8725384f48   

                                                                                                                                      Filepath  \
41  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Janus\Janus_Part_5\Cue_0045.jbp   

   Data_Components_0_m_Colony_text Data_Components_1_m_Colony_text  \
41                                                                   

   Data_Components_2_m_Colony_text Planet_Name Data_Components_0_m_Item_text  \
41                                                                             

   Data_Components_1_m_Item_text Data_Components_2_m_Item_text  \
41                                                               

   Data_Components_3_m_Item_text Data_OnShow_Actions_0_m_ItemToGive_text  \
41                                                                         

   Data_OnStop_Actions_0_m_ItemToGive_text         Item_Name  \
41                        Lilaethan's Fury  Lilaethan's Fury   

                                                  All_AssetId  \
41  nan, nan, nan, nan, nan, 1ca7c664e50c4ba39b55b294d5765d84   

                        Item_AssetId  
41  1ca7c664e50c4ba39b55b294d5765d84

   Projects_data    


Empty DataFrame
Columns: [AssetId, Data_$type, Data_ActionsOnFinish_Actions_0_$type, Data_ActionsOnFinish_Actions_0_Etude, Data_ActionsOnFinish_Actions_0_Trait, Data_ActionsOnFinish_Actions_0_Value_$type, Data_ActionsOnFinish_Actions_0_Value_Value, Data_ActionsOnFinish_Actions_0_Value_name, Data_ActionsOnFinish_Actions_0_m_Chronicle, Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint, Data_ActionsOnFinish_Actions_0_m_Flag, Data_ActionsOnFinish_Actions_0_name, Data_ActionsOnFinish_Actions_1_$type, Data_ActionsOnFinish_Actions_1_Etude, Data_ActionsOnFinish_Actions_1_m_Chronicle, Data_ActionsOnFinish_Actions_1_m_ColonyBlueprint, Data_ActionsOnFinish_Actions_1_m_NewVisualBlueprint, Data_ActionsOnFinish_Actions_1_m_Planet, Data_ActionsOnFinish_Actions_1_m_ProductivityPercents, Data_ActionsOnFinish_Actions_1_name, Data_ActionsOnFinish_Actions_2_$type, Data_ActionsOnFinish_Actions_2_Etude, Data_ActionsOnFinish_Actions_2_name, Data_ActionsOnFinish_Actions_3_$type, Data_ActionsOnFinish_Actions_3_Status, Data_ActionsOnFinish_Actions_3_m_Objective, Data_ActionsOnFinish_Actions_3_name, Data_ActionsOnFinish_Actions_4_$type, Data_ActionsOnFinish_Actions_4_m_Achievement, Data_ActionsOnFinish_Actions_4_name, Data_AvailabilityConditions_Conditions_0_$type, Data_AvailabilityConditions_Conditions_0_Playing, Data_AvailabilityConditions_Conditions_0_Started, Data_AvailabilityConditions_Conditions_0_Unit_$type, Data_AvailabilityConditions_Conditions_0_Unit_name, Data_AvailabilityConditions_Conditions_0_m_Cue, Data_AvailabilityConditions_Conditions_0_m_Direction, Data_AvailabilityConditions_Conditions_0_m_Etude, Data_AvailabilityConditions_Conditions_0_m_Fact, Data_AvailabilityConditions_Conditions_0_name, Data_AvailabilityConditions_Conditions_1_$type, Data_AvailabilityConditions_Conditions_1_NotStarted, Data_AvailabilityConditions_Conditions_1_Playing, Data_AvailabilityConditions_Conditions_1_Unit_$type, Data_AvailabilityConditions_Conditions_1_Unit_name, Data_AvailabilityConditions_Conditions_1_m_Etude, Data_AvailabilityConditions_Conditions_1_m_Fact, Data_AvailabilityConditions_Conditions_1_name, Data_AvailabilityConditions_Operation, Data_Components_0_$type, Data_Components_0_Faction, Data_Components_0_NewCost, Data_Components_0_Reputation, Data_Components_0_m_AddToParty, Data_Components_0_m_ApplyToAllColonies, Data_Components_0_m_Colony, Data_Components_0_m_ContentmentModifier, Data_Components_0_m_Count, Data_Components_0_m_EfficiencyModifier, Data_Components_0_m_Fact, Data_Components_0_m_Item, Data_Components_0_m_NotBuiltProject, Data_Components_0_m_Objective, Data_Components_0_m_ProfitFactor, Data_Components_0_m_Resource_Count, Data_Components_0_m_Resource_Resource, Data_Components_0_m_SecurityModifier, Data_Components_0_m_Spawners_0_Spawner_EntityNameInEditor, Data_Components_0_m_Spawners_0_Spawner_SceneAssetGuid, Data_Components_0_m_Spawners_0_Spawner__entity_id, Data_Components_0_m_Spawners_0_m_EnterPoint, Data_Components_0_m_Spawners_1_Spawner_EntityNameInEditor, Data_Components_0_m_Spawners_1_Spawner_SceneAssetGuid, Data_Components_0_m_Spawners_1_Spawner__entity_id, Data_Components_0_m_Spawners_1_m_EnterPoint, Data_Components_0_m_Spawners_2_Spawner_EntityNameInEditor, Data_Components_0_m_Spawners_2_Spawner_SceneAssetGuid, Data_Components_0_m_Spawners_2_Spawner__entity_id, Data_Components_0_m_Spawners_2_m_EnterPoint, Data_Components_0_m_Spawners_3_Spawner_EntityNameInEditor, Data_Components_0_m_Spawners_3_Spawner_SceneAssetGuid, Data_Components_0_m_Spawners_3_Spawner__entity_id, Data_Components_0_m_Spawners_3_m_EnterPoint, Data_Components_0_m_Spawners_4_Spawner_EntityNameInEditor, Data_Components_0_m_Spawners_4_Spawner_SceneAssetGuid, Data_Components_0_m_Spawners_4_Spawner__entity_id, Data_Components_0_m_Spawners_4_m_EnterPoint, Data_Components_0_m_Spawners_5_Spawner_EntityNameInEditor, Data_Components_0_m_Spawners_5_Spawner_SceneAssetGuid, Data_Components_0_m_Spawners_5_Spawner__entity_id, Data_Components_0_m_Spawners_5_m_EnterPoint, Data

projects_data_full = projects_data.merge(dialogs_merged[['Data_m_BlueprintDialog','Item_Name','Planet_Name']],
                                         left_on = ['Data_ActionsOnFinish_Actions_0_m_Chronicle', 'Planet_Name'],
                                         right_on=['Data_m_BlueprintDialog','Planet_Name'],
                                         how = 'right',
                                         suffixes=('_x','_y'))

#### format dialog _items table for export

In [953]:
#check for missing values
missing_values_tab(dialogs_merged[['Item_AssetId','Item_Name', 'Planet_Name']])

Dataframe contains 3 columns and 146 strings.

It has  0 columns with missed values


Empty DataFrame
Columns: [missed_values, %_of_all, data_type]
Index: []

In [954]:
# Select only rows where Planet_Name and Item_Name not empty
dialog_items_table = dialogs_merged.query('Item_Name!=""').query('Planet_Name!=""')[['Item_AssetId','Item_Name', 'Planet_Name']]
dialog_items_table = dialog_items_table.drop_duplicates()
display(dialog_items_table)

Item_AssetId  \
0    2612a899accd40faa1639661c2a1b7f0   
3    6e851ded713b408aae6d2a64d5a1f4ae   
12   ae1b0709a966449d88140165d5c7bbbe   
18   edda83161cb64980ba542ab004da1552   
27   da06e0225ea646f89f926f9eaaa7ed28   
31   0c3d2a3a6f8c4b8f9c372f5a34823cc9   
33   cb0a37f32de7486dbc79824d65dca7f8   
41   722fc682ec7d4e0386f28158c2ca8acf   
43   843b3ed725d4470da4e7791fd86fb827   
45   b748125e691946bf9f9f68ea588fbc52   
49   a346d0ed1a074155a9d06bb4ffac13e7   
55   dfd380bab20f47dc9f4368eccc76ee30   
80   c56a979981ca4d6b85c8251c28864391   
85   0d6b5ecf6a9d43e2bd5f38fa6f5bd9d0   
111  03e596b0191b4573b94e3b7fd582ff1a   
118  2dfb8d2dbcd047609f1056856d585d35   
120  1c20a615e0f04591a467b8a62aea1996   
123  9e129aa1b6244db7b567ee028247d2ec   
124  7f65081576c749ada80ab498002b987b   
130  9743b66895f946d98592e11390b78a0f   
140  0bc113c3a2a54e7d9b865b4bfe2809b5   

                                                                                                                                                                                                                               Item_Name  \
0    This ancient component of a Dargonus-fleet frigate was discovered in the wastes by the Engine Vandals and presented to the Rogue Trader.\nTorpedo tubes capable of firing 5 short-burning plasma torpedoes with 19 damage warheads.   
3                                                                                                                                                                                                                      Wasteland Twister   
12                                                                                                                                                                                                                          Psychic Ward   
18                                                                                                                                                                                                                 Book of Minor Prayers   
27                                                                                                                                                                                                               Saint Cognatius's Relic   
31                                                                                                                                                                                                                        Malpian Shroud   
33                                                                                                                                                                                                                     Righteous Justice   
41                                                                                                                                                                                                                 Crucible-Born Tempest   
43                                                                                                                                                                                                   Assault Adamantine Voidship Plating   
45                                                                                                                                                                                                         Saint Cognatius's Ostensorium   
49                                                                                                                                                                                                                      Triumph of Faith   
55                                                                                                                                                                                                                 Heart of the Nameless   
80                                                    

In [955]:
dialog_items_table['Dialog_Item_Location'] = dialog_items_table['Planet_Name'] +', construction events'

In [956]:
display(dialog_items_table)

Item_AssetId  \
0    2612a899accd40faa1639661c2a1b7f0   
3    6e851ded713b408aae6d2a64d5a1f4ae   
12   ae1b0709a966449d88140165d5c7bbbe   
18   edda83161cb64980ba542ab004da1552   
27   da06e0225ea646f89f926f9eaaa7ed28   
31   0c3d2a3a6f8c4b8f9c372f5a34823cc9   
33   cb0a37f32de7486dbc79824d65dca7f8   
41   722fc682ec7d4e0386f28158c2ca8acf   
43   843b3ed725d4470da4e7791fd86fb827   
45   b748125e691946bf9f9f68ea588fbc52   
49   a346d0ed1a074155a9d06bb4ffac13e7   
55   dfd380bab20f47dc9f4368eccc76ee30   
80   c56a979981ca4d6b85c8251c28864391   
85   0d6b5ecf6a9d43e2bd5f38fa6f5bd9d0   
111  03e596b0191b4573b94e3b7fd582ff1a   
118  2dfb8d2dbcd047609f1056856d585d35   
120  1c20a615e0f04591a467b8a62aea1996   
123  9e129aa1b6244db7b567ee028247d2ec   
124  7f65081576c749ada80ab498002b987b   
130  9743b66895f946d98592e11390b78a0f   
140  0bc113c3a2a54e7d9b865b4bfe2809b5   

                                                                                                                                                                                                                               Item_Name  \
0    This ancient component of a Dargonus-fleet frigate was discovered in the wastes by the Engine Vandals and presented to the Rogue Trader.\nTorpedo tubes capable of firing 5 short-burning plasma torpedoes with 19 damage warheads.   
3                                                                                                                                                                                                                      Wasteland Twister   
12                                                                                                                                                                                                                          Psychic Ward   
18                                                                                                                                                                                                                 Book of Minor Prayers   
27                                                                                                                                                                                                               Saint Cognatius's Relic   
31                                                                                                                                                                                                                        Malpian Shroud   
33                                                                                                                                                                                                                     Righteous Justice   
41                                                                                                                                                                                                                 Crucible-Born Tempest   
43                                                                                                                                                                                                   Assault Adamantine Voidship Plating   
45                                                                                                                                                                                                         Saint Cognatius's Ostensorium   
49                                                                                                                                                                                                                      Triumph of Faith   
55                                                                                                                                                                                                                 Heart of the Nameless   
80                                                    

## Appendix

### Service queries

English version:

In [957]:
# search text by strinkey 7dd797bddb414f7684c7608bd7f1943f
index_df.query('index == "7d66fd6f-89ba-46d7-bd56-a2efd6e68407"')['text']

25106    This ancient component of a Dargonus-fleet frigate was discovered in the wastes by the Engine Vandals and presented to the Rogue Trader.\n{g|Encyclopedia:TorpedoLaunchersSpace}Torpedo tubes{/g} capable of firing 5 short-burning plasma torpedoes with 19 {g|Encyclopedia:SpaceBattleDamageGlossary}d...
Name: text, dtype: object

In [958]:
#search filepath by file's asset id 
assets_df.query('AssetId=="25a86da04d1d43a6b7da07180cd51cf7"')['File']

8362    e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Janus\Janus_Part_5\Janus_Part_5.jbp
Name: File, dtype: object

Finding a particular value in dataframe:

In [959]:
colonization_data[colonization_data.eq("30ba329178714fe1bdd570ddb7868509").any(axis = 1)]

AssetId  \
1114  e61dc2e5c3cf4a0f93e2821ff855a2e2   
1156  30ba329178714fe1bdd570ddb7868509   
1157  9440a44bed5e41baa8a43cd7d0aedc85   
2295  7a18dbdfd91644edbfab2c8a870f6eed   

                                                      Data_$type  \
1114              8eee9d45ddcfa614d99610c1892993e3, BlueprintCue   
1156           c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog   
1157  72b026d82361459581a0cb453c0385cb, BlueprintColonyChronicle   
2295    86139952581c4e7fa135794685e236f9, BlueprintColonyProject   

      Data_AccessibilityModifier Data_ActionsOnFinish_Actions  \
1114                         NaN                          NaN   
1156                         NaN                          NaN   
1157                         NaN                          NaN   
2295                         NaN                          NaN   

                  Data_ActionsOnFinish_Actions_0_$type  \
1114                                               NaN   
1156                                               NaN   
1157                                               NaN   
2295  1fd3c7ebaa8a499d9e5f7ac9a43bf6af, StartChronicle   

     Data_ActionsOnFinish_Actions_0_Etude  \
1114                                  NaN   
1156                                  NaN   
1157                                  NaN   
2295                                  NaN   

      Data_ActionsOnFinish_Actions_0_EtudeEvaluator  \
1114                                            NaN   
1156                                            NaN   
1157                                            NaN   
2295                                            NaN   

     Data_ActionsOnFinish_Actions_0_Evaluate  \
1114                                     NaN   
1156                                     NaN   
1157                                     NaN   
2295                                     NaN   

     Data_ActionsOnFinish_Actions_0_Trait  \
1114                                  NaN   
1156                                  NaN   
1157                                  NaN   
2295                                  NaN   

     Data_ActionsOnFinish_Actions_0_UnlockIfNot  \
1114                                        NaN   
1156                                        NaN   
1157                                        NaN   
2295                                        NaN   

     Data_ActionsOnFinish_Actions_0_Value_$type  \
1114                                        NaN   
1156                                        NaN   
1157                                        NaN   
2295                                        NaN   

      Data_ActionsOnFinish_Actions_0_Value_Value  \
1114                                         NaN   
1156                                         NaN   
1157                                         NaN   
2295                                         NaN   

     Data_ActionsOnFinish_Actions_0_Value_name  \
1114                                       NaN   
1156                                       NaN   
1157                                       NaN   
2295                                       NaN   

     Data_ActionsOnFinish_Actions_0_m_Chronicle  \
1114                                        NaN   
1156                                        NaN   
1157                                        NaN   
2295           30ba329178714fe1bdd570ddb7868509   

     Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint  \
1114                                              NaN   
1156                                              NaN   
1157                                              NaN   
2295                 876fc13fdc10492b8444e045ac8f9ecc   

     Data_ActionsOnFinish_Actions_0_m_Flag  \
1114                                   NaN   
1156                                   NaN   
1157                                   NaN   
2295                                   NaN   

                   Data_ActionsOnFinish_Actions_0_name  \
1114                                  

Russian version:

In [960]:
index_df_ru.query('index == "b3ed026f-d2d0-40cb-a54d-85d1c7f63507"')['text']

36273    В Просторе Коронус нет более достойно{mf|го|й} опекун{mf|а|ши} для обители веры, чем глава династии фон Валанциус. В столице мира в е{mf|го|е} честь будет возведена великолепная базилика, украшенная грандиозной парной скульптурой Императора и Вольного Торговца. Тысячи прихожан и жрецов будут пом...
Name: text, dtype: object

:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\KiavaGamma\KiavaGamma_Part_5_true\Answer_0015.jbp

In [961]:
# search in projects_data table
display(projects_data.query('Project_Name=="Touched by Holiness"'))

AssetId  \
50  7dd797bddb414f7684c7608bd7f1943f   

                                                  Data_$type  \
50  86139952581c4e7fa135794685e236f9, BlueprintColonyProject   

   Data_ActionsOnFinish_Actions_0_$type Data_ActionsOnFinish_Actions_0_Etude  \
50                                  NaN                                  NaN   

   Data_ActionsOnFinish_Actions_0_Trait  \
50                                  NaN   

   Data_ActionsOnFinish_Actions_0_Value_$type  \
50                                        NaN   

   Data_ActionsOnFinish_Actions_0_Value_Value  \
50                                        NaN   

   Data_ActionsOnFinish_Actions_0_Value_name  \
50                                       NaN   

   Data_ActionsOnFinish_Actions_0_m_Chronicle  \
50                                        NaN   

   Data_ActionsOnFinish_Actions_0_m_ColonyBlueprint  \
50                                              NaN   

   Data_ActionsOnFinish_Actions_0_m_Flag Data_ActionsOnFinish_Actions_0_name  \
50                                   NaN                                 NaN   

   Data_ActionsOnFinish_Actions_1_$type Data_ActionsOnFinish_Actions_1_Etude  \
50                                  NaN                                  NaN   

   Data_ActionsOnFinish_Actions_1_m_Chronicle  \
50                                        NaN   

   Data_ActionsOnFinish_Actions_1_m_ColonyBlueprint  \
50                                              NaN   

   Data_ActionsOnFinish_Actions_1_m_NewVisualBlueprint  \
50                                                 NaN   

   Data_ActionsOnFinish_Actions_1_m_Planet  \
50                                     NaN   

   Data_ActionsOnFinish_Actions_1_m_ProductivityPercents  \
50                                                   NaN   

   Data_ActionsOnFinish_Actions_1_name Data_ActionsOnFinish_Actions_2_$type  \
50                                 NaN                                  NaN   

   Data_ActionsOnFinish_Actions_2_Etude Data_ActionsOnFinish_Actions_2_name  \
50                                  NaN                                 NaN   

   Data_ActionsOnFinish_Actions_3_$type Data_ActionsOnFinish_Actions_3_Status  \
50                                  NaN                                   NaN   

   Data_ActionsOnFinish_Actions_3_m_Objective  \
50                                        NaN   

   Data_ActionsOnFinish_Actions_3_name Data_ActionsOnFinish_Actions_4_$type  \
50                                 NaN                                  NaN   

   Data_ActionsOnFinish_Actions_4_m_Achievement  \
50                                          NaN   

   Data_ActionsOnFinish_Actions_4_name  \
50                                 NaN   

   Data_AvailabilityConditions_Conditions_0_$type  \
50                                            NaN   

   Data_AvailabilityConditions_Conditions_0_Playing  \
50                                              NaN   

   Data_AvailabilityConditions_Conditions_0_Started  \
50                                              NaN   

   Data_AvailabilityConditions_Conditions_0_Unit_$type  \
50                                                 NaN   

   Data_AvailabilityConditions_Conditions_0_Unit_name  \
50                                                NaN   

   Data_AvailabilityConditions_Conditions_0_m_Cue  \
50                                            NaN   

   Data_AvailabilityConditions_Conditions_0_m_Direction  \
50                                                  NaN   

   Data_AvailabilityConditions_Conditions_0_m_Etude  \
50                                              NaN   

   Data_AvailabilityConditions_Conditions_0_m_Fact  \
50                                             NaN   

   Data_AvailabilityConditions_Conditions_0_name  \
50                                           NaN   

   Data_AvailabilityConditions_Conditions_1_$type  \
50                                            NaN   

   Data_AvailabilityConditions_Conditions_1_NotStarted  \

In [962]:
index_df.query('text.str.contains("Sky Barrier")')

index         text
4593  1706c4e8-c57c-41fd-ac12-7defce8fb7e1  Sky Barrier

### Saving

In [963]:
#projects_items_table.to_csv(save_folder + r'\project_items_df_eng.csv', index = False)
#dialog_items_table.to_csv(save_folder + r'\dialog_items_table_eng.csv', index = False)

_______

#finding the file with a particular string searching through folders:
from pathlib import Path

path = Path(work_folder)

search_string = '1ca7c664e50c4ba39b55b294d5765d84'

for o in path.rglob('*.jbp'):
    if o.is_file():
        text = o.read_text()
        if search_string in text:
            print(o)
            print(text)

e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Janus\Janus_Part_4\Answer_0007.jbp

```e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Janus\Janus_Part_4\Answer_0007.jbp
{
  "AssetId": "380d37dafb104b2988e26a75dffa94de",
  "Data": {
    "$type": "df78945bb9f434e40b897758499cb714, BlueprintAnswer",
    "PrototypeLink": "",
    "m_Overrides": [],
    "Components": [
      {
        "$type": "2aa503c54af44bd5b74037ea4f833dfb, RewardChangeStatEfficiency",
        "name": "$RewardChangeStatEfficiency$c4a8a479-702f-40df-9173-19b97ab63540",
        "m_Flags": 0,
        "PrototypeLink": {
          "guid": "",
          "name": ""
        },
        "m_Overrides": [],
        "HideInUI": false,
        "m_EfficiencyModifier": -1,
        "m_ApplyToAllColonies": false,
        "m_Colony": "!bp_47400e8140a3434882459f2c95b54b7f"
      },
      {
        "$type": "2a09d956d9324196867de1714fc59e1e, RewardChangeStatContentment",
        "name": "$RewardChangeStatContentment$4588afd7-87ce-402b-af4b-9edcf9551b93",
        "m_Flags": 0,
        "PrototypeLink": {
          "guid": "",
          "name": ""
        },
        "m_Overrides": [],
        "HideInUI": false,
        "m_ContentmentModifier": -1,
        "m_ApplyToAllColonies": false,
        "m_Colony": "!bp_47400e8140a3434882459f2c95b54b7f"
      },
      {
        "$type": "34bf31b8b1354678ac0d3db2f79f2831, RewardChangeStatSecurity",
        "name": "$RewardChangeStatSecurity$f0d54194-076f-43e0-b224-f5174c8adc63",
        "m_Flags": 0,
        "PrototypeLink": {
          "guid": "",
          "name": ""
        },
        "m_Overrides": [],
        "HideInUI": false,
        "m_SecurityModifier": -1,
        "m_ApplyToAllColonies": false,
        "m_Colony": "!bp_47400e8140a3434882459f2c95b54b7f"
      }
    ],
    "Comment": "",
    "ParentAsset": "afb30cf036a44b87b7476b6f0ec5d48d",              link to id of answer list file
    "SoulMarkRequirement": {
      "Direction": "None",
      "Value": 0,
      "CheckByRank": false,
      "Rank": 0,
      "Description": {
        "m_Key": "",
        "m_OwnerString": "",
        "m_OwnerPropertyPath": "",
        "m_JsonPath": "",
        "Shared": null
      }
    },
    "Text": {
      "m_Key": "01720db3-ee44-40ce-b7dc-ad7efcbac36a",                     phrase in dialog
      "m_OwnerString": "380d37dafb104b2988e26a75dffa94de",
      "m_OwnerPropertyPath": "Text",
      "m_JsonPath": "Strings/Mechanics/Blueprints\\GlobalMaps\\Colonization\\Colonization_Narrative\\ColonyChronicles\\Janus\\Janus_Part_4\\Answer_0007_Text.json",
      "Shared": null
    },
    "NextCue": {
      "Cues": [
        "!bp_68610952acec428591d010ba9d49b744"                       link to asset id of the file with answer to the phrase in m_Key
      ],
      "Strategy": "First"
    },
    "ShowOnce": false,
    "ShowOnceCurrentDialog": false,
    "ShowCheck": {
      "Type": "Unknown",
      "DC": 0
    },
    "OnCheckSuccess": {
      "Actions": []
    },
    "OnCheckFail": {
      "Actions": []
    },
    "DebugMode": false,
    "CharacterSelection": {
      "SelectionType": "Clear",
      "ComparisonStats": []
    },
    "ShowConditions": {
      "Operation": "Or",
      "Conditions": []
    },
    "SelectConditions": {
      "Operation": "And",
      "Conditions": []
    },
    "RequireValidCue": false,
    "AddToHistory": true,
    "OnSelect": {
      "Actions": [
        {
          "$type": "2ac5d227b9415e94d959e0c8198646db, ApplyTraitToColony",
          "name": "$ApplyTraitToColony$d7a318c2-ca84-45c4-83a1-b66c3e1449de",
          "Trait": "!bp_1deaf516f6254f24aee2dfe85a4a81a6",
          "m_Colony": "!bp_47400e8140a3434882459f2c95b54b7f"      link to assetid of the planet  
        }
      ]
    },
    "Description": {
      "m_Key": "",
      "m_OwnerString": "",
      "m_OwnerPropertyPath": "",
      "m_JsonPath": "",
      "Shared": null
    },
    "FakeChecks": [],
    "SoulMarkShift": {
      "Direction": "Faith",
      "Value": 0,
      "CheckByRank": false,
      "Rank": 0,
      "Description": {
        "m_Key": "",
        "m_OwnerString": "",
        "m_OwnerPropertyPath": "",
        "m_JsonPath": "",
        "Shared": null
      }
    }
  },
  "Meta": {
    "ShadowDeleted": false
  }
}```

file with project 'Sky barrier'
```e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Projects\Strategical\PrSt46_StrategicalProject.jbp```

## Prototype function to search stringkeys in python
filename = r'e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Projects\Stage\PrStage18_StageProject.jbp'
with open(filename) as asset_file:           
                file_contents = asset_file.read()
                data = json.loads(file_contents)
def find_parent(D):
    """find first key path to value containing stringkey"""    
    for k, v in D.items():        
            if isinstance(v,dict):
                parent = find_parent(v)
                if parent:
                    return [k] + parent
            elif match_pattern(v):                
                return [k]
find_parent(data)                

def find_parents(D):
    """Find all key pathes to values containing string values"""    
    output = []
    result = []
    for k, v in D.items(): 
        if k not in output:
            if isinstance(v,dict):
                parent = find_parents(v)
                if parent:
                    if parent not in output:
                           output.append([k] + parent)
                           
            elif match_pattern(v):
                if v not in output:
                    output.append([k])   
    return output                          

def flatten(A):   
    rt = []
    for i in A:
        if isinstance(i, list):rt.extend(flatten(i))
        else: rt.append(i)
    #rt.insert(0,'Data')
    return rt             

output = find_parents(data) 
flatten(output[0][1])   

In [964]:
weapons_data = pd.read_csv(save_folder + r'\weapons_data_eng.csv')
weapons_data = weapons_data.fillna('')

In [965]:
weapons_data.query('Item_Name.str.contains("Lilaethan")')

AssetId  \
127  4027957aa0bb430091cf555d3d09052f   
394  1ca7c664e50c4ba39b55b294d5765d84   

                                                Data_$type  \
127  c00f723cccf2d314198c42a572c631fd, BlueprintItemWeapon   
394  c00f723cccf2d314198c42a572c631fd, BlueprintItemWeapon   

     Data_AbilityContainer_Ability1_AP Data_AbilityContainer_Ability1_Mode  \
127                                  1                             Default   
394                                  1                             Default   

    Data_AbilityContainer_Ability1_OnHitOverrideType  \
127                                             None   
394                                             None   

    Data_AbilityContainer_Ability1_Type  \
127                          SingleShot   
394                          SingleShot   

    Data_AbilityContainer_Ability1_m_Ability  \
127         a489b6d823ef4b86b431aa1d42e385c7   
394         9dec1bdade284190b0977f5f70d26d3e   

    Data_AbilityContainer_Ability1_m_OnHitActions  \
127                                                 
394                                                 

     Data_AbilityContainer_Ability2_AP Data_AbilityContainer_Ability2_Mode  \
127                                  2                             Default   
394                                  0                             Default   

    Data_AbilityContainer_Ability2_OnHitOverrideType  \
127                                             None   
394                                             None   

    Data_AbilityContainer_Ability2_Type  \
127                              Custom   
394                                None   

    Data_AbilityContainer_Ability2_m_Ability  \
127         8fe7633db25d46a8bebc2868b8acff12   
394                                            

    Data_AbilityContainer_Ability2_m_OnHitActions  \
127                                                 
394                                                 

     Data_AbilityContainer_Ability3_AP Data_AbilityContainer_Ability3_Mode  \
127                                  4                                 Any   
394                                  0                             Default   

    Data_AbilityContainer_Ability3_OnHitOverrideType  \
127                                             None   
394                                             None   

    Data_AbilityContainer_Ability3_Type  \
127                              Reload   
394                                None   

    Data_AbilityContainer_Ability3_m_Ability  \
127         98f4a31b68e446ad9c63411c7b349146   
394                                            

    Data_AbilityContainer_Ability3_m_OnHitActions  \
127                                                 
394                                                 

     Data_AbilityContainer_Ability4_AP Data_AbilityContainer_Ability4_Mode  \
127                                  0                             Default   
394                                  0                             Default   

    Data_AbilityContainer_Ability4_OnHitOverrideType  \
127                                             None   
394                                             None   

    Data_AbilityContainer_Ability4_Type  \
127                                None   
394                                None   

    Data_AbilityContainer_Ability4_m_Ability  \
127                                            
394                                            

     Data_AbilityContainer_Ability5_AP Data_AbilityContainer_Ability5_Mode  \
127                                  0                             Default   
394                                  0                             Default   

    Data_AbilityContainer_Ability5_OnHitOverrideType  \
127                                             None   
394                                             None   

    Data_AbilityContainer_Ability5_Type  \
127                                None   
394                              

In [966]:
"""
colonization_narratives_folder = r'e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles'
dir_list = next(os.walk(colonization_narratives_folder))[1]
list_of_dialog_files = []
list_of_cues_files = []
list_of_answerlist_files = []
list_of_check_files = []
list_of_answer_files = []
for root,dirs,files in os.walk(colonization_narratives_folder):
        for file in files:
            if 'Cue_' in file:
                  list_of_cues_files.append(os.path.join(root, file))
            elif 'Check_' in file:
                  list_of_check_files.append(os.path.join(root, file))
            elif 'AnswersList' in file:
                  list_of_answerlist_files.append(os.path.join(root, file))
            elif 'Answer_' in file:
                  list_of_answer_files.append(os.path.join(root, file))
            else:
                  if 'Sequence' not in file:
                        list_of_dialog_files.append(os.path.join(root, file))  
"""


"\ncolonization_narratives_folder = r'e:\\Steam\\RogueTrader\\WorkFolder\\Blueprints\\GlobalMaps\\Colonization\\Colonization_Narrative\\ColonyChronicles'\ndir_list = next(os.walk(colonization_narratives_folder))[1]\nlist_of_dialog_files = []\nlist_of_cues_files = []\nlist_of_answerlist_files = []\nlist_of_check_files = []\nlist_of_answer_files = []\nfor root,dirs,files in os.walk(colonization_narratives_folder):\n        for file in files:\n            if 'Cue_' in file:\n                  list_of_cues_files.append(os.path.join(root, file))\n            elif 'Check_' in file:\n                  list_of_check_files.append(os.path.join(root, file))\n            elif 'AnswersList' in file:\n                  list_of_answerlist_files.append(os.path.join(root, file))\n            elif 'Answer_' in file:\n                  list_of_answer_files.append(os.path.join(root, file))\n            else:\n                  if 'Sequence' not in file:\n                        list_of_dialog_files.append

In [967]:
#Create cues df
cues_df = colonization_data[colonization_data['Data_$type']=="8eee9d45ddcfa614d99610c1892993e3, BlueprintCue"]
cues_df = drop_trash_columns(cues_df)
keyword = ['$type','Answer','ParentAsset','Cue','Continue']
drop_columns = []
for col in cues_df.columns:
    if keyword[0] not in col and keyword[1] not in col and keyword[2] not in col and keyword[3] not in col and keyword[4] not in col:
        drop_columns.append(col)
columns = [x for x in cues_df.columns if x not in drop_columns]
cues_df = cues_df[['AssetId'] + columns + ['Filepath']]
    


In [968]:
#Creating table with  Data_$type=='c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog':
dialogs_df = colonization_data[colonization_data['Data_$type']=="c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog"]
dialogs_df = dialogs_df.replace('[]',np.nan)
dialogs_df = drop_trash_columns(dialogs_df)
print('Dialogs_df'.center(20))
display(dialogs_df.head())
#Create cues df
cues_df = colonization_data[colonization_data['Data_$type']=="8eee9d45ddcfa614d99610c1892993e3, BlueprintCue"]
cues_df = cues_df.replace('[]',np.nan)
cues_df = drop_trash_columns(cues_df)

print('Cues_df'.center(20))
display(cues_df.head())
#Create df with Data_$type=="52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList"
answer_lists_df = colonization_data[colonization_data['Data_$type']=="52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList"]
answer_lists_df = answer_lists_df.replace('[]',np.nan)
answer_lists_df = drop_trash_columns(answer_lists_df)
print('AnswerLists'.center(20))
display(answer_lists_df.head())

     Dialogs_df     


AssetId  \
89   d5e49c0bbd67405a8c8aaa22bb9cfcf7   
133  06fb6b96d1ca4611b28b4c94283029f3   
174  28270a72320f4a6591a3715abb610fb0   
214  59fd079d48b34b449af0f8fbf1074e89   
326  f899fe78721d408bb35105cbc2197e6f   

                                            Data_$type  \
89   c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog   
133  c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog   
174  c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog   
214  c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog   
326  c8ff73feae580b142a9f43e0c61d7f32, BlueprintDialog   

    Data_Conditions_Conditions_0_$type Data_Conditions_Conditions_0_Not  \
89                                 NaN                              NaN   
133                                NaN                              NaN   
174                                NaN                              NaN   
214                                NaN                              NaN   
326                                NaN                              NaN   

    Data_Conditions_Conditions_0_m_Colony Data_Conditions_Conditions_0_name  \
89                                    NaN                               NaN   
133                                   NaN                               NaN   
174                                   NaN                               NaN   
214                                   NaN                               NaN   
326                                   NaN                               NaN   

    Data_Conditions_Conditions_1_$type Data_Conditions_Conditions_1_Playing  \
89                                 NaN                                  NaN   
133                                NaN                                  NaN   
174                                NaN                                  NaN   
214                                NaN                                  NaN   
326                                NaN                                  NaN   

    Data_Conditions_Conditions_1_Started Data_Conditions_Conditions_1_m_Etude  \
89                                   NaN                                  NaN   
133                                  NaN                                  NaN   
174                                  NaN                                  NaN   
214                                  NaN                                  NaN   
326                                  NaN                                  NaN   

    Data_Conditions_Conditions_1_name Data_Conditions_Operation  \
89                                NaN                       And   
133                               NaN                       And   
174                               NaN                       And   
214                               NaN                       And   
326                               NaN                       And   

                    Data_FinishActions_Actions_0_$type  \
89   727d31d013cf5d34eac20031d87ee75c, FinishChronicle   
133  727d31d013cf5d34eac20031d87ee75c, FinishChronicle   
174  727d31d013cf5d34eac20031d87ee75c, FinishChronicle   
214  727d31d013cf5d34eac20031d87ee75c, FinishChronicle   
326  727d31d013cf5d34eac20031d87ee75c, FinishChronicle   

    Data_FinishActions_Actions_0_m_Chronicle  \
89          d1de65f37fc64aa78484f1023d734dcf   
133         b5968802fe0a4dcf82773009d10172b8   
174         27f7cebf0eb346afa9d635f5a135a7b4   
214         65e58f202b6d420bbbab24b3185a77db   
326         5f9cd4235eb94258b7663e545a97090e   

    Data_FinishActions_Actions_0_m_ColonyBlueprint  \
89                e433f1613297486cb6ddec834f37dd95   
133               e433f1613297486cb6ddec834f37dd95   
174               e433f1613297486cb6ddec834f37dd95   
214               e433f1613297486cb6ddec834f37dd95   
326               e433f1613297486cb6ddec834f37dd95   

                     Data_FinishActions_Actions_0_name  \
89   $FinishChronicle$8b3698ecb6384bb9889141a68129002c   
133  $FinishChronicle$e2da7604b8674ed5a9392d4c74b3c974   
174  $

      Cues_df       


AssetId  \
64  5b088d2f604541cabab01b0f30aeb836   
65  ab5d213f67a44088afbd16be1a010bb1   
66  c0a439da574e48d7804ce4427a138e09   
67  68b38f32cfdc42d6a0dff65030b2a8a7   
68  e1a1abbf7fe7495c847783c1867cec75   

                                        Data_$type  \
64  8eee9d45ddcfa614d99610c1892993e3, BlueprintCue   
65  8eee9d45ddcfa614d99610c1892993e3, BlueprintCue   
66  8eee9d45ddcfa614d99610c1892993e3, BlueprintCue   
67  8eee9d45ddcfa614d99610c1892993e3, BlueprintCue   
68  8eee9d45ddcfa614d99610c1892993e3, BlueprintCue   

   Data_AlignmentShift_Direction Data_Animation  \
64                           NaN           None   
65                           NaN           None   
66                           NaN           None   
67                           NaN           None   
68                           NaN           None   

                      Data_Answers_0 Data_Conditions_Conditions_0_$type  \
64  7326cd8552094a37b0ada5754a5d1816                                NaN   
65  7326cd8552094a37b0ada5754a5d1816                                NaN   
66                               NaN                                NaN   
67                               NaN                                NaN   
68                               NaN                                NaN   

   Data_Conditions_Conditions_0_MatchWhenActive  \
64                                          NaN   
65                                          NaN   
66                                          NaN   
67                                          NaN   
68                                          NaN   

   Data_Conditions_Conditions_0_MatchWhenDetached  \
64                                            NaN   
65                                            NaN   
66                                            NaN   
67                                            NaN   
68                                            NaN   

   Data_Conditions_Conditions_0_MatchWhenRemote  \
64                                          NaN   
65                                          NaN   
66                                          NaN   
67                                          NaN   
68                                          NaN   

   Data_Conditions_Conditions_0_Not Data_Conditions_Conditions_0_Playing  \
64                              NaN                                  NaN   
65                              NaN                                  NaN   
66                              NaN                                  NaN   
67                              NaN                                  NaN   
68                              NaN                                  NaN   

   Data_Conditions_Conditions_0_Started Data_Conditions_Conditions_0_m_Answer  \
64                                  NaN                                   NaN   
65                                  NaN                                   NaN   
66                                  NaN                                   NaN   
67                                  NaN                                   NaN   
68                                  NaN                                   NaN   

   Data_Conditions_Conditions_0_m_Check Data_Conditions_Conditions_0_m_Cue  \
64                                  NaN                                NaN   
65                                  NaN                                NaN   
66                                  NaN                                NaN   
67                                  NaN                                NaN   
68                                  NaN                                NaN   

   Data_Conditions_Conditions_0_m_Etude  \
64                                  NaN   
65                                  NaN   
66                                  NaN   
67                                  NaN   
68                                  NaN   

   Data_Conditions_Conditions_0_m_Project  \
64                                    NaN   
65        

    AnswerLists     


AssetId  \
54   7326cd8552094a37b0ada5754a5d1816   
93   093ae79c7e9046e38aae60128f8f83de   
137  7c46c72e02f64ffb9fd248791fd9b02b   
177  8a1b1a01af9f437b88472f4457d1ea0f   
218  3ea02262d53f4d4da44134e15b2b5976   

                                                 Data_$type  \
54   52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList   
93   52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList   
137  52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList   
177  52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList   
218  52ca6275d0a87bf428811a8c24d89de4, BlueprintAnswersList   

    Data_AlignmentRequirement                    Data_Answers_0  \
54                        NaN  4068cab8ec99418d905301cc9b803060   
93                        NaN  b4e5b8932b814482ad7aa37f5be98dec   
137                       NaN  7bb14d1981594d3daa84225c993ce409   
177                       NaN  33cae5d538ca4f0d886ab0092cd78d54   
218                       NaN  5c2c12ab5fb4408ca23c73271ab0194a   

                       Data_Answers_1 Data_Answers_10 Data_Answers_11  \
54   a0d948be8d94456ba4d59066c2608e80             NaN             NaN   
93   b25c32a7784c46efa76db2337b327a46             NaN             NaN   
137  b36077fd301c4c02a3eddd70066e18c9             NaN             NaN   
177  e911ddf985264b41811e42253e41cbfd             NaN             NaN   
218  545471d129684007a90716e140408e06             NaN             NaN   

                       Data_Answers_2                    Data_Answers_3  \
54   8b0daca6abc240ccaaa97d2eb93444e8  08f07a9a15ab49888f8679f2ece63aba   
93   ded4379ce18c4fcc856025ae40a1e84c  1f20217bc203421b8314e1b61c07f54a   
137  1299398af2b74895a59c5ff62b4e8332  b5b1d2945ed4483baaa87b0c15357c5b   
177  decb61867a484afa9ef12e1bd4fdfcb1  444c7009ff6f4e5581e4ac4d716a651a   
218  e0ea48bbd8444d7b8e280f652b343d31  3ed46fab88664a4493a85c2cbd30dc17   

                       Data_Answers_4                    Data_Answers_5  \
54   beefd62b39b642e4b6c3f4f08ba515bc  12317ce8b1044d0984c70c4a06a160b3   
93   f9511e44854c402eaa120c21ff01c4df  eba0ac4eb7fb4b9e8da1a6905cd4e6ed   
137  9e2408928c72448c95f70edf1c0cf9f9  d18489e1a44b446c8d0ab2535203e9b0   
177  b3123323163c40f5957c4533b3cb8a43  7500194cffa24290a39b1529ba462f63   
218  2adacc9d1d184327924eb52f2a2b90b6  8f1c43cc4bf44d138403518478a5cdc9   

                       Data_Answers_6                    Data_Answers_7  \
54   3ef55abc14194780aca3a7752cd9f015  f5fdf9f8c2eb4acd97bff670b6c4ef49   
93   a662fd86a25e467185f7f2c73f103f66  2e86c423435642baa975d0af07df95e2   
137  2306c70b2e734f1d936a668c36705b3c  d391406566e9428f937ee47890a78a98   
177  1c2823d8525246f1a48d3f2227a6d73f                               NaN   
218                               NaN                               NaN   

                       Data_Answers_8 Data_Answers_9  \
54                                NaN            NaN   
93   817f65c979094863a0073c013708e7f3            NaN   
137  4d94270503954a29b9f979508eb13ef2            NaN   
177                               NaN            NaN   
218                               NaN            NaN   

    Data_Conditions_Operation                  Data_ParentAsset  \
54                        And  5b088d2f604541cabab01b0f30aeb836   
93                        And  9852af25b58542adad20a4dc09641fc4   
137                       And  de50d46474e045019c75849b9b50c034   
177                       And  b7559d334f4c427c90dd1cf76a00b0ee   
218                       And  45f36b828f3f44fda84561896cd93a81   

    Data_SoulMarkRequirement_Direction  \
54                                None   
93                                None   
137                               None   
177                               None   
218                               None   

                                                                                                                                                     Filepath  
54   e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMa

In [973]:
temp_df.head()

AssetId                  Data_ParentAsset  \
0  4068cab8ec99418d905301cc9b803060  7326cd8552094a37b0ada5754a5d1816   
1  08f07a9a15ab49888f8679f2ece63aba  7326cd8552094a37b0ada5754a5d1816   
2  12317ce8b1044d0984c70c4a06a160b3  7326cd8552094a37b0ada5754a5d1816   
3  f5fdf9f8c2eb4acd97bff670b6c4ef49  7326cd8552094a37b0ada5754a5d1816   
4  8b0daca6abc240ccaaa97d2eb93444e8  7326cd8552094a37b0ada5754a5d1816   

                                                                                                                                              Filepath  
0  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Answer_0001.jbp  
1  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Answer_0003.jbp  
2  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Answer_0004.jbp  
3  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Answer_0005.jbp  
4  e:\Steam\RogueTrader\WorkFolder\Blueprints\GlobalMaps\Colonization\Colonization_Narrative\ColonyChronicles\Dargonus\Dargonus_Part_1\Answer_0006.jbp